# Cleaning CC data

This python notebook operates on a csv created after editing in open refine and is designed to finish cleaning columns of interest which were easier to clean in python.

# [Resume Here](#resumehere)

<a id='TOC'></a>

# Table of Contents

1. [Outstanding Problems](#outstanding)

1. [Setting up Python](#SettingUp)
    
    1. [Setting the Location](#SettingLoc)
    
    2. [Importing Data](#ImportingData)
    
    3. [Preparing for a Save](#PreparingSave)
    
4. [Functions](#Functions)
    
2. [Inspecting the Data](#InspectingData)
3. [Cleaning Data](#CleaningData)
    1. [Column-by-Column Cleaning](#ColbyCol)
        1. [rtl](#rtl)
        2. [tl](#tl)
        3. [svl](#svl)
        4. [autotomized](#autotomized)
        5. [toes](#toes)
        6. [sex](#sex)
        7. [species](#species)
        7. [new.recap](#newrecap)
        8. [date](#date)
    2. [Correcting class of columns](#CorrectingClass)
    
4. [Adding Columns](#AddCol)

    1. [TL_SVL](#TlSvl)
    
    2. [Mass_SVL](#MassSvl)
    
    3. [Lizard Number](#LizardNumber)
    
    4. [Days Since Capture](#daysSinceCapture)

    5. [Number of Captures](#capture)

5. [Export Cleaned Data](#exportFinal)

<a id='outstanding'></a>

# Outstanding Problems

1. [outstanding1](#outstanding1)
2. [outstanding2](#outstanding2)
3. [outstanding3](#outstanding3)
4. [outstanding4](#outstanding4)

<a id='SettingUp'></a>

# Setting up Python

[Top](#TOC)

Here we import necessary packages. 
This chunk may take a while.

In [1]:
import pandas as pd
import numpy as np
import os
from liz_number import lizsort,mindate,smallest,validate
from liz_toes import make_str,label_pattern, replace_pattern,report_pattern

import plotly
import plotly.plotly as py
import plotly.graph_objs as go

plotly.tools.set_config_file(world_readable=True)

# increase print limit
pd.options.display.max_rows = 99999
pd.options.display.max_columns = 50

<a id='SettingLoc'></a>

## Setting the location
[Top](#TOC)

These chunks identify the locations from which we can get data and to which we can save data.

## Source Data
Source files can be found in the following locations:

In [2]:
sourceDataPers = 'C:/Users/Christopher/Google Drive/TailDemography/Cleaned Combined Data'
sourceDataBig = 'S:/Chris/TailDemography/TailDemography/Cleaned Combined Data'
# sourceBlack = 'C:/Users/test/Desktop'

### Intermediate Source Data
Intermediate files can be found in the following locations:

In [3]:
sourceInterDataPers = 'C:/Users/Christopher/Google Drive/TailDemography/Intermediate Files/DeepCleaning'
sourceinterDataBig = 'S:/Chris/TailDemography/TailDemography/Intermediate Files/DeepCleaning'
# sourceBlack = 'C:/Users/test/Desktop'

## Output Data paths
Outputfiles can be found in the following locations:

In [4]:
outputPers = 'C:/Users/Christopher/Google Drive/TailDemography/outputFiles'
outputBig = 'S:/Chris/TailDemography/TailDemography/outputFiles'
# outputBlack = 'C:/Users/test/Desktop'

<a id='ImportingData'></a>

## Importing data
[Top](#TOC)

Here we import data from one of the available locations

In [5]:
os.chdir(sourceDataBig)
df=pd.read_csv('Appended and Trimmed CC Data 2000-2017_2019-01-07 19hrs22min.csv')
df.head()

species       toes sex        date svl   tl rtl  autotomized mass  \
0      sj  2-6-12-15   m    19vi2010  80  110  29          3.0   20   
1      sj  2-9-15-17   f  13viii2010  56   77   0          1.0  5.5   
2      sj  3-6-11-17   m  18viii2010  50   68   0          1.0    4   
3      sj  3-6-15-16   f  18viii2010  72   62  46          3.0   11   
4      sj  3-6-12-17   m  18viii2010  57   82   0          1.0    6   

                                         location meters new.recap painted  \
0                               10m v bottom bowl    -15         ?     yes   
1                                      20m up CCC    240       NEW     yes   
2                           1m vT at top R island    157       NEW     yes   
3  halfway between pool and 2 falls 2m up rt side    385       NEW     yes   
4                               R outcrop ^ oak R    425       new     yes   

   sighting paint.mark      vial                                       misc  
0       NaN        y2c  03-10-cc  toe 15 missing at capture; possible recap  
1       NaN       y62c  61-10-cc                                        Tss  
2       NaN      y<c.t       NaN                             Bss; lost toes  
3       NaN       y65c  65-10-cc                                        NaN  
4       NaN       y67c  66-10-cc                                        NaN

<a id='PreparingSave'></a>

## Preparing for a save
[Top](#TOC)

Now we change the working directory so that inermediate files are saved to our preferred location.

In [6]:
os.chdir(sourceinterDataBig)
df.head()

species       toes sex        date svl   tl rtl  autotomized mass  \
0      sj  2-6-12-15   m    19vi2010  80  110  29          3.0   20   
1      sj  2-9-15-17   f  13viii2010  56   77   0          1.0  5.5   
2      sj  3-6-11-17   m  18viii2010  50   68   0          1.0    4   
3      sj  3-6-15-16   f  18viii2010  72   62  46          3.0   11   
4      sj  3-6-12-17   m  18viii2010  57   82   0          1.0    6   

                                         location meters new.recap painted  \
0                               10m v bottom bowl    -15         ?     yes   
1                                      20m up CCC    240       NEW     yes   
2                           1m vT at top R island    157       NEW     yes   
3  halfway between pool and 2 falls 2m up rt side    385       NEW     yes   
4                               R outcrop ^ oak R    425       new     yes   

   sighting paint.mark      vial                                       misc  
0       NaN        y2c  03-10-cc  toe 15 missing at capture; possible recap  
1       NaN       y62c  61-10-cc                                        Tss  
2       NaN      y<c.t       NaN                             Bss; lost toes  
3       NaN       y65c  65-10-cc                                        NaN  
4       NaN       y67c  66-10-cc                                        NaN

<a id='Functions'></a>

# Functions
[Back to: Top](#TOC)

1. [appendstr](#appenstr)
2. [typeordrop](#typeordrop)
3. [myint](#myint)
3. [testint](#testint)
4. [rom2arab](#rom2arab)
5. [exportliz](#exportliz)

<a id = 'appendstr'></a>

## appendstr
[Back to Top](#TOC)

[Back to Functions](#Functions)

In [7]:
def appendstr(x, value, connector = '', position='end'):
    """
    appends *value* and *x* separated by a *connector* with the position of *val* determined by *position*
    :param x:
    :param value:
    :param connector:
    :param position:
    """
    assert((isinstance(x,str)|(x is None)|(x!=x))),"x must be str type, NoneType or NaN: x is {} type."\
    .format(type(x))
    if ((x!=x)|(x is None)):
        x=''
    assert(isinstance(value,str)),"value must be str type: value is {} type.".format(type(value))
    assert(isinstance(connector,str))\
    , "connector must be str or None type, not {} type.".format(type(connector))
    assert(isinstance(position,(str,int))), "position must be either str or int type, not {}."\
           .format(type(position))           
    if isinstance(position,str):
        assert(position in ['start','end']), "If position is str type, it must be either 'start' or 'end'."
        positiondict = {'start':0,'end':len(x)}
        position = positiondict[position]
    if isinstance(position,int):
        assert(position in range(0,1+len(x)))\
        , "If position is int type, it must be a value in the range 0 through {}.".format(len(x))
    prefix = x[:position]
    suffix = x[position:]
    if len(x)==0:
        res = value
    else:
        if position == 0:
            res = prefix+value+connector+suffix
        if position == len(x):
            res = prefix+connector+value+suffix
        if (position>0&position<1):
            res = prefix+connector+value+connector+suffix

    return res
    

Here's an example of how *appendstr* works.

In [8]:
foo='bar'
appendstr(foo,'test',connector='_',position=1)

'b_test_ar'

In [9]:
appendstr(foo,'test',connector='_',position=1)

'b_test_ar'

In [10]:
appendstr(None,'test',connector='_',position='end')

'test'

In [11]:
appendstr(None,'test',position=0)

'test'

[back to Functions](#Functions)

<a id='typeordrop'></a>

## typeordrop
[Back to Top](#TOC)

[Back to Functions](#Functions)

In [12]:
def typeordrop(x,typ,replace=None, verbose=True):
    """this function attempts to force an object, *x*, to a particular type,*typ*. If this is not possible, 
    it reports the value of the object that could not be forced and replaces the object with the value 
    supplied to the *replace* argument"""
    if not isinstance(x,typ)==True:
        while False:
            try:
                x=typ(x)
                print("Working as expected")
                break
            except TypeError:
                if verbose==True:
                    print("Could not force value supplied to 'x' argument to {} type. x is {} type:\n\n x = {}"\
                          .format(typ,type(x),x))
                x = replace
    else:
        print("{} is already of type {}.".format(x,typ))
    return x
         

Here are a few examples of how *typeordrop* works.

In [13]:
x=['foo','bar']
typeordrop(x,int)

['foo', 'bar']

[back to Functions](#Functions)

<a id='myint'></a>

## myint
[Back to Top](#TOC)

[Back to Functions](#Functions)

In [14]:
def myint(x, verbose = False):
    try:
        x = str(x).split('.')[0]
    except:
        x = x
        if verbose == True:
            print('{} is of type {} and cannot be forced to int.'.format(x,type(x)))
    return x


Here is are a few examples of how [*myint*](#myint) works.

In [15]:
bar = [None, 1.0, "f"]
print([type(x) for x in bar])
[myint(x) for x in bar]

[<class 'NoneType'>, <class 'float'>, <class 'str'>]


['None', '1', 'f']

In [16]:
bar = [None, 2001.0, "2001.0"]
print([type(x) for x in bar])
[myint(x,True) for x in bar]

[<class 'NoneType'>, <class 'float'>, <class 'str'>]


['None', '2001', '2001']

[back to Functions](#Functions)

<a id = 'testint'></a>
## testint

[Back to Top](#TOC)

[Back to Functions](#Functions)

In [17]:
def testint(x):
    try:
        res = int(x)
    except:
        res = x
    return res

In [18]:
foo = ['9ix2010', '2ii2010', '10vii2011','30viii2009','30-9-2011']
foo = pd.DataFrame(foo).rename(columns={0:'date'})
dict_rom2arab = {'i':'1','ii':'2','iii':'3','iv':'4','v':'5','vi':'6','vii':'7','viii':'8','ix':'9','x':'10'
        ,'xi':'11','xii':'12'}
print(dict_rom2arab.keys())
foo

dict_keys(['i', 'ii', 'iii', 'iv', 'v', 'vi', 'vii', 'viii', 'ix', 'x', 'xi', 'xii'])


date
0     9ix2010
1     2ii2010
2   10vii2011
3  30viii2009
4   30-9-2011

In [19]:
testint(3)

3

In [20]:
testint('r')

'r'

In [21]:
[isinstance(testint(char),int) for char in foo.date[0]]

[True, False, False, True, True, True, True]

In [22]:
[isinstance(testint(char),int) for char in foo.date[4]]

[True, True, False, True, False, True, True, True, True]

[back to Functions](#Functions)

<a id = 'rom2arab'></a>

## rom2arab
[Back to Top](#TOC)

[Back to Functions](#Functions)

In [23]:
def rom2arab(x,new_dict= None, verbose = False, replace = False):
    """checks keys in new_dict to determine which keys the string portion of, x, and replaces the at string with 
    the corresponding value in new_dict."""
    dict_rom2arab = {'i':'01','ii':'02','iii':'03','iv':'04','v':'05','vi':'06','vii':'07','viii':'08'
                     ,'ix':'09','x':'10','xi':'11','xii':'12'}
    if new_dict is None:
        new_dict = dict_rom2arab 
    idx_str = [isinstance(testint(char),int) for char in x]
    idx_tmp = range(0,len(x))
    str_df = pd.DataFrame({'numeric':idx_str,'index':idx_tmp})
    idx_strings = str_df.loc[str_df.numeric==False,'index']
    idx_numeric = str_df.loc[str_df.numeric==True,'index']
    val2replace = x[idx_strings.min():idx_strings.max()+1] # This assumes that all string values are contiuguos.
    try:
        newval = '-'+new_dict[val2replace]+'-'
        if verbose is True:
            res =["replaced value: \'{}\'".format(val2replace),x.replace(val2replace,newval)]
        else:
            res = x.replace(val2replace,newval)
    except:
        res = x
        if verbose is True:
            print("x has no string values contained in 'new_dict'. \nx:{}".format(x))
    return res


In [24]:
rom2arab(foo.date[0],verbose=False)

'9-09-2010'

In [25]:
rom2arab(foo.date[0],verbose=True)

["replaced value: 'ix'", '9-09-2010']

In [26]:
rom2arab(foo.date[4],verbose=True)

x has no string values contained in 'new_dict'. 
x:30-9-2011


'30-9-2011'

In [27]:
foo.date.apply(rom2arab)

0     9-09-2010
1     2-02-2010
2    10-07-2011
3    30-08-2009
4     30-9-2011
Name: date, dtype: object

[back to Functions](#Functions)

<a id = 'exportliz'></a>

## exportliz
[Back to Top](#TOC)

[Back to Functions](#Functions)

In [192]:
def exportliz(df,iterator, lizard = None, prefix = None, verbose = False):
    """creates a filename for each lizards and then saves that lizards data to that filename. 
    Can take a list of lizards or iterate over the entire dataframe"""
    assert isinstance(df,pd.DataFrame), "df must be pandas DataFrame, not {}.".format(type(df))
    assert ((lizard is None) |(isinstance(lizard,list))), "lizard must be Nonetype or list, not {}.".format(lizard)
    assert ((prefix is None) |(isinstance(prefix,str))), "lizard must be Nonetype or str, not {}.".format(lizard)
    assert iterator in df.columns, "iterator must be in df.columns:\n {}".format(df.columns)
    if prefix is None:
        prefix = "File for lizard " 
    suffix = ".csv"
    if lizard is not None:
        assert lizard in df[iterator].unique(), "lizard must be None or contained in df[iterator]."
        for liz in lizard:
            filename = prefix + str(liz) + suffix
            if verbose == True:
                print("liz type:{}\nliz:{}\ndf[iterator]:{}".format(type(liz),liz,type(df[iterator])))
            data = df.loc[df[iterator] == liz,:]
            data.to_csv(filename)
    else:
        for liz in pd.unique(df[iterator]):
            filename = prefix + str(liz) + suffix
            if verbose == True:
                print("liz:{}\nliz:{}\ndf[iterator]:{}".format(type(liz),liz,type(df[iterator])))
            data = df.loc[df[iterator] == liz,:]
            data.to_csv(filename)

<a id= 'InspectingData'></a>

[back to Functions](#Functions)

## Inspecting the Data
[Top](#TOC)

Let's take a look at the data.

In [28]:
print("\nThere are {} data points in our data set.".format(df.shape[0]))


There are 6299 data points in our data set.


In [29]:
print("\nThe columns in the data have the following data types:\n{}".format(df.dtypes))


The columns in the data have the following data types:
species         object
toes            object
sex             object
date            object
svl             object
tl              object
rtl             object
autotomized    float64
mass            object
location        object
meters          object
new.recap       object
painted         object
sighting       float64
paint.mark      object
vial            object
misc            object
dtype: object


<a id= 'CleaningData'></a>

# Cleaning the Data
[Back to: Top](#TOC)

Now we get to the actual cleaning of the data.  We will inspect the data and take the appropriate cleaning steps:
1. [Column-by-Column Cleaning](#ColbyCol)

2. [Correcting class of columns](#CorrectingClass)

<a id='ColbyCol'></a>

## Column-by-Column Cleaning
[Back to: Top](#TOC)

We will handle the cleaning for each column in this section.
1. [rtl](#rtl)
2. [tl](#tl)
3. [svl](#svl)
4. [autotomized](#autotomized)
    1. [creating 'rtl_orig'and relabeling 'rtl' and 'autotomized](#rtlRTL_ORIGautotomized)
    2. [copy the values in rtl to a new column, *rtl_orig*](#copyrtl)
    3. [relabel entries in the autotomized column based on the values in the rtl_orig column](#relabelaut) 
    4. [relabel entries in the rtl column](#relabelrtl)
5. [toes](#toes)
6. [sex](#sex)
7. [species](#species)
8. [new.recap](#newrecap)
9. [date](#date)

<a id='rtl'></a>

## 'rtl' 
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

Here we investigate and clean values in the column 'rtl'. These should be int type values that are greater than or equal to -1.  First, we test to see if all of the values are of type int.

In [30]:
badtypes = []
for val in df.rtl:
    try:
        x = isinstance(type(int(val)),int)
    except:
        badtypes=badtypes+[val]
print("'badtypes' represents {} entries in the df:".format(len(badtypes)))
if len(badtypes)==0:
    print("\nAll values in df.rtl can be successfuly converted to int.\n\n")
#     df['rtl'] = df.rtl.apply(int)
else:
    print("\nAll values in df.rtl could not be converted to int.  The following values could not be \
converted and should be investigated:\n\n{}\n\nbadtypes values are distributed as follows in the df:\n\n{}"\
          .format(list(set(badtypes)),df.loc[df.rtl.isin(badtypes),'rtl'].value_counts(dropna=False)))

'badtypes' represents 3596 entries in the df:

All values in df.rtl could not be converted to int.  The following values could not be converted and should be investigated:

[nan, '-', '?', '32 -12', '10(kink)', 'o']

badtypes values are distributed as follows in the df:

NaN         3590
?              2
32 -12         1
10(kink)       1
-              1
o              1
Name: rtl, dtype: int64


The non-NaN values are few, so we will inspect these first.

In [31]:
pd.set_option('max_colwidth',100000)
df.loc[(df.rtl.isin(badtypes))&(df.rtl.notna()),:]

species         toes sex                 date svl  tl       rtl  \
884       sj          NaN   m  2003-04-19 00:00:00  56  32         ?   
907       sj   4-10-14-18   m  2003-04-30 00:00:00  76  19         ?   
1037      sv    1-6-11-20   m  2003-06-27 00:00:00  41  60         o   
6097      uo       4-6-18   m  2004-07-12 00:00:00  52  75    32 -12   
6193      sv          NaN   f  2004-07-21 00:00:00   -   -         -   
6220      sj    2-9-12-18   f  2004-07-22 00:00:00  65  94  10(kink)   

      autotomized mass                         location meters new.recap  \
884           NaN  NaN                        talus 326    326       NEW   
907           NaN  NaN                         wall 15m     15     recap   
1037          NaN    4               sb 5m ^ cave trail     50       NEW   
6097          NaN  4.7  sb opp fallen juniper -> flat R    208       new   
6193          NaN    6                      sb @ cc/ccc    240     recap   
6220          NaN  9.4    wall rt side v wall v cave tr    NaN     recap   

      painted  sighting paint.mark    vial  \
884   painted       NaN        b7c     NaN   
907   painted       NaN        b9a     NaN   
1037  painted       NaN        sMb     NaN   
6097  painted       NaN        w^c   04-63   
6193  painted       NaN      w148b     NaN   
6220  painted       NaN      w154b     NaN   

                                                    misc  
884                                                  NaN  
907            9 looks like a backwards P and t combined  
1037       lost toes for vial, accidently cut off toe 11  
6097  blue throat and blue belly; accidentally cut toe 6  
6193                                             escaped  
6220                 hurt toes 11-13 in capture; Bss Tss

Based on review discussions, we will make the changes below:
- ‘?’--> 0; misc: “unsure if tail was recently broken at very tip”
- ‘o’--> 0
- ‘32 -12’ -->32; misc: “potential double-break at 12 \[george to check before use\]” 
- ‘-’--> NaN
- ‘10(kink)’-->0; misc:”kink at 10mm”
We will use the function [*appendstr*](#appendstr) to do this.

"‘?’--> 0; misc: “unsure if tail was recently broken at very tip”

In [32]:
idx_ques = (df.rtl.isin(badtypes))&(df.rtl=='?')
df[idx_ques]

species         toes sex                 date svl  tl rtl  autotomized  \
884      sj          NaN   m  2003-04-19 00:00:00  56  32   ?          NaN   
907      sj   4-10-14-18   m  2003-04-30 00:00:00  76  19   ?          NaN   

    mass   location meters new.recap  painted  sighting paint.mark vial  \
884  NaN  talus 326    326       NEW  painted       NaN        b7c  NaN   
907  NaN   wall 15m     15     recap  painted       NaN        b9a  NaN   

                                          misc  
884                                        NaN  
907  9 looks like a backwards P and t combined

In [33]:
df.loc[idx_ques,'misc']= df.loc[idx_ques,:].misc\
.apply(lambda x: appendstr(x,"unsure if tail was recently broken at very tip",';'))
df.loc[idx_ques,'rtl']= '0'

These entries now look like this:

In [34]:
df.loc[idx_ques,:]

species         toes sex                 date svl  tl rtl  autotomized  \
884      sj          NaN   m  2003-04-19 00:00:00  56  32   0          NaN   
907      sj   4-10-14-18   m  2003-04-30 00:00:00  76  19   0          NaN   

    mass   location meters new.recap  painted  sighting paint.mark vial  \
884  NaN  talus 326    326       NEW  painted       NaN        b7c  NaN   
907  NaN   wall 15m     15     recap  painted       NaN        b9a  NaN   

                                                                                          misc  
884                                             unsure if tail was recently broken at very tip  
907  9 looks like a backwards P and t combined;unsure if tail was recently broken at very tip;

"‘o’--> 0"

In [35]:
idx_o = (df.rtl.isin(badtypes))&(df.rtl=='o')
df[idx_o]

species        toes sex                 date svl  tl rtl  autotomized  \
1037      sv   1-6-11-20   m  2003-06-27 00:00:00  41  60   o          NaN   

     mass            location meters new.recap  painted  sighting paint.mark  \
1037    4  sb 5m ^ cave trail     50       NEW  painted       NaN        sMb   

     vial                                           misc  
1037  NaN  lost toes for vial, accidently cut off toe 11

In [36]:
df.loc[idx_o,'rtl']= '0'

These entries now look like this:

In [37]:
df.loc[idx_o,:]

species        toes sex                 date svl  tl rtl  autotomized  \
1037      sv   1-6-11-20   m  2003-06-27 00:00:00  41  60   0          NaN   

     mass            location meters new.recap  painted  sighting paint.mark  \
1037    4  sb 5m ^ cave trail     50       NEW  painted       NaN        sMb   

     vial                                           misc  
1037  NaN  lost toes for vial, accidently cut off toe 11

"‘32-12’ -->32; misc: “potential double-break at 12 \[george to check before use\]"

In [38]:
idx_32 = (df.rtl.isin(badtypes))&(df.rtl=='32 -12')
df.loc[idx_32]

species     toes sex                 date svl  tl     rtl  autotomized  \
6097      uo   4-6-18   m  2004-07-12 00:00:00  52  75  32 -12          NaN   

     mass                         location meters new.recap  painted  \
6097  4.7  sb opp fallen juniper -> flat R    208       new  painted   

      sighting paint.mark    vial  \
6097       NaN        w^c   04-63   

                                                    misc  
6097  blue throat and blue belly; accidentally cut toe 6

In [39]:
df.loc[idx_32,'misc']= df.loc[idx_32,:].misc\
.apply(lambda x: appendstr(x,"potential double-break at 12 [george to check before use]",';'))

df.loc[idx_32,'rtl']= '32'

These entries now look like this:

In [40]:
df.loc[idx_32,:]

species     toes sex                 date svl  tl rtl  autotomized mass  \
6097      uo   4-6-18   m  2004-07-12 00:00:00  52  75  32          NaN  4.7   

                             location meters new.recap  painted  sighting  \
6097  sb opp fallen juniper -> flat R    208       new  painted       NaN   

     paint.mark    vial  \
6097        w^c   04-63   

                                                                                                               misc  
6097  blue throat and blue belly; accidentally cut toe 6;potential double-break at 12 [george to check before use];

"‘-’-->'NaN'"

In [41]:
idx_minus = (df.rtl.isin(badtypes))&(df.rtl=='-')
df.loc[idx_minus,:]

species toes sex                 date svl tl rtl  autotomized mass  \
6193      sv  NaN   f  2004-07-21 00:00:00   -  -   -          NaN    6   

         location meters new.recap  painted  sighting paint.mark vial     misc  
6193  sb @ cc/ccc    240     recap  painted       NaN      w148b  NaN  escaped

We will also address the values for svl and tl in this row.

In [42]:
df.loc[idx_minus,['rtl','tl','svl']]= np.nan

These entries now look like this:

In [43]:
df.loc[idx_minus,:]

species toes sex                 date  svl   tl  rtl  autotomized mass  \
6193      sv  NaN   f  2004-07-21 00:00:00  NaN  NaN  NaN          NaN    6   

         location meters new.recap  painted  sighting paint.mark vial     misc  
6193  sb @ cc/ccc    240     recap  painted       NaN      w148b  NaN  escaped

‘10(kink)’-->0; misc:”kink at 10mm” We will use the function appendstr to do this."

In [44]:
idx_10kink = (df.rtl.isin(badtypes))&(df.rtl=='10(kink)')
df.loc[idx_10kink,:]

species       toes sex                 date svl  tl       rtl  \
6220      sj  2-9-12-18   f  2004-07-22 00:00:00  65  94  10(kink)   

      autotomized mass                       location meters new.recap  \
6220          NaN  9.4  wall rt side v wall v cave tr    NaN     recap   

      painted  sighting paint.mark vial                                 misc  
6220  painted       NaN      w154b  NaN  hurt toes 11-13 in capture; Bss Tss

In [45]:
df.loc[idx_10kink,'misc']= df.loc[idx_10kink,:].misc.apply(lambda x: appendstr(x,"kink at 10mm",';'))
df.loc[idx_10kink,'rtl']= '0'

These entries now look like this:

In [46]:
df.loc[idx_10kink,:]

species       toes sex                 date svl  tl rtl  autotomized  \
6220      sj  2-9-12-18   f  2004-07-22 00:00:00  65  94   0          NaN   

     mass                       location meters new.recap  painted  sighting  \
6220  9.4  wall rt side v wall v cave tr    NaN     recap  painted       NaN   

     paint.mark vial                                               misc  
6220      w154b  NaN  hurt toes 11-13 in capture; Bss Tss;kink at 10mm;

Now we will inspect those that had at least one other length measurement (svl or tl).

In [47]:
pd.reset_option('max_colwidth')
idx_rtlnaplus1 = (df.rtl.isna())&(((df.svl.isna())&~(df.tl.isna()))|(~(df.svl.isna())&(df.tl.isna())))
df.loc[idx_rtlnaplus1]

species       toes  sex                 date    svl   tl  rtl  \
2027      sj  2-6-13-20    f  2001-03-23 00:00:00    ~70  NaN  NaN   
4642      sj        NaN    m  2002-03-16 00:00:00  large  NaN  NaN   
4814      sj        NaN  NaN  2002-03-17 00:00:00  large  NaN  NaN   
5175      sj        NaN    f  2002-03-20 00:00:00  large  NaN  NaN   
5640      sj        NaN    m  2002-03-19 00:00:00  large  NaN  NaN   
5784      sv        NaN    ?  2002-03-19 00:00:00  small  NaN  NaN   

      autotomized mass                                     location meters  \
2027          NaN  NaN                   bottom R wall v cave trail     30   
4642          NaN  NaN  active in crevice in wall 3m v juniper xing    112   
4814          NaN  NaN                                          H4a    194   
5175          NaN  NaN                           L across from wall    318   
5640          NaN  NaN                            up rt wall @ pool    NaN   
5784          NaN  NaN                                sb 4m ^ flatR    NaN   

     new.recap painted  sighting paint.mark  \
2027  sighting     NaN       NaN          ?   
4642  sighting     NaN       NaN          ?   
4814  sighting     NaN       NaN     w85a??   
5175  sighting     NaN       NaN       w||t   
5640  sighting     NaN       NaN        ???   
5784  sighting     NaN       NaN        NaN   

                                                   vial  \
2027  could read toes 6,13 for certain; toe 2 uncert...   
4642                                                NaN   
4814                                                NaN   
5175                                                NaN   
5640                                                NaN   
5784                                                NaN   

                                          misc  
2027                                       NaN  
4642                                       NaN  
4814  probably w85a but could only see the "5"  
5175                                       NaN  
5640            ~25mm original T; rest regrown  
5784                   had moth so didn'tcatch

All but one of these was a sighting.  We will have to look at the field notes to confirm whether or not data were actually missing for the remaining entry.

In [48]:
df.loc[(df.rtl.isna())&((df.svl.notna())|(df.tl.notna()))&df['new.recap'].str.contains('recap'),:]

species          toes sex                 date svl  tl  rtl  autotomized  \
5907      sv  1-6-16-17-20   m  2004-07-04 00:00:00  52  53  NaN          NaN   

     mass      location meters new.recap  painted  sighting paint.mark vial  \
5907  3.6  bottom chute    355     recap  painted       NaN        w.t  NaN   

           misc  
5907  few mites

Once we have addressed these, we will force rtl to an int type.

Now we check to see for out of range rtl values, *i.e.* rtl values less than -1 or suspiciously high.

We will exclude 0 and -1 values for rtl in these figures because of the large proportion of in range values they account for.

In [49]:
dfnobadtypes0neg1 = (~df.rtl.isin(badtypes))&(~df.rtl.isin(['0','-1']))
dfother = ~(df.species.dropna().str.contains('v|j'))&(df.species.notna())&(dfnobadtypes0neg1)
jarrovii = go.Histogram(x = df.loc[(df.species.str.contains('j'))&(dfnobadtypes0neg1)
                                   ,'rtl'].astype(int, 'ignore'),name = 'S. jarrovii',xbins =dict(size=1)
                        #,histnorm='probability'
                        , cumulative=dict(enabled = False, direction = 'increasing'))
virgatus = go.Histogram(x = df.loc[(df.species.str.contains('v'))&(dfnobadtypes0neg1)
                                   ,'rtl'].astype(int, 'ignore'), name = 'S. virgatus',xbins =dict(size=1)
                       #,histnorm='probability'
                        , cumulative=dict(enabled = False, direction = 'increasing'))
other = go.Histogram(x = df.loc[dfother,'rtl'].astype(int, 'ignore'), name = 'other',xbins =dict(size=1)
                                  #,histnorm='probability'
                     , cumulative=dict(enabled = False
                                                                           , direction = 'increasing'))
data = [jarrovii, virgatus,other]
layout = go.Layout(
    title = 'Histogram of rtl by species',
    titlefont = dict(
        size = 20),
    xaxis = dict(
        dtick = 1,
        title = 'rtl (mm)',
        titlefont = dict(
            size = 18)),
    yaxis = dict(
        title = 'Number of Lizards',
        titlefont = dict(
            size = 18))
)
fig = go.Figure(
        data = data,
        layout = layout)
py.iplot(fig, filename = 'Histogram of rtl by species (new)')

Perhaps it's worth inspecting values greater than 50. 

In [50]:
idx_dfabove50 = (df.species.str.contains('j|v'))&(~df.rtl.isin(badtypes))\
&(df.loc[(~df.rtl.isin(badtypes)),'rtl'].astype(int, 'ignore')>=50)
df[idx_dfabove50]

species               toes sex                 date  svl  tl rtl  \
419       sj           5-11-18    M  2014-07-03 00:00:00   85  73  56   
634       sj         5-10-11-16   m  2000-03-20 00:00:00   81  93  55   
773       sj             2-8-13   F  2012-05-25 00:00:00   82  79  57   
779       sj             3-9-15   f  2012-05-28 00:00:00   79  85  58   
901       sj            2-12-17   m  2003-04-30 00:00:00   89  97  56   
1193      sj          4-9-12-20   m  2003-07-02 00:00:00   81  62  50   
1582      sj          4-9-12-20   m  2003-07-18 00:00:00   78  65  50   
1844      sj         2 - 8 - 13   F  2011-06-21 00:00:00   70  73  54   
1846      sj         3 - 9 - 15   F  2011-06-23 00:00:00   75  82  56   
1853      sj    1 - 7 - 14 - 19   M  2011-06-19 00:00:00   80  73  52   
1867      sj       b 1 - 7 - 11   F  2011-06-20 00:00:00  7.5  70  90   
1873      sj  b 2 - 9 - 15 - 17   F  2011-06-20 00:00:00  7.6  68  86   
2010      sj          1-7-13-16   f  2001-03-22 00:00:00   75  64  50   
2130      sj         5-10-15-16   m  2001-07-13 00:00:00   93  82  58   
2562       j          5-7-13-16   m  2015-07-06 00:00:00   78  75  55   
3964      sj          1-15-19 a   m  2008-07-08 00:00:00   90  70  50   
4022      sj            1-15-19   m  2008-07-18 00:00:00   89  70  50   
4322       j          5-7-13-16   m  2016-05-10 00:00:00   80  80  60   
4433      sj            2-12-17   m  2002-07-03 00:00:00   87  93  54   
4435      sj         4-10-14-18   m  2002-07-03 00:00:00   66  69  50   
5832      sj          4-9-12-20   m  2004-07-02 00:00:00   85  66  52   
6065      sj          4-9-12-20   m  2004-07-10 00:00:00   80  68  52   

      autotomized  mass                              location meters  \
419           NaN  19.5                               black r    171   
634           NaN  15.5                                2falls    NaN   
773           NaN  21.5                        loose on T; H5    NaN   
779           NaN  19.3                                1falls    NaN   
901           NaN   NaN                                1falls      1   
1193          NaN  18.5        alligator juniper @top of site    452   
1582          NaN  17.5                  Rs across from oak R    418   
1844          NaN  10.4                    stream bed 2m v H5    198   
1846          NaN   7.7                  right Rs bottom bowl     -7   
1853          NaN    20                             opp oak R    418   
1867          NaN     0          3m right side ^ Juniper Xing    118   
1873          NaN     0                    10m up CCC on slab    250   
2010          NaN  11.2                                 chute    358   
2130          NaN  24.8                    Rs 3m v cave trail     42   
2562          NaN  14.8                         SB 8m v bowl     -16   
3964          NaN    23     leftR outcrop 5m v downed juniper    215   
4022          NaN  21.7  large Rs opp and 3m v downed juniper    217   
4322          NaN  14.7                               R in sb    -20   
4433          NaN  17.6                    wall 20m ^ 1 falls     20   
4435          NaN   8.6                      sb 20m ^ 1 falls     20   
5832          NaN    22              leaning juniper 7m v top    452   
6065          NaN  21.2                    5m v rock with oak    440   

     new.recap                                            painted  sighting  \
419        new                                                yes       NaN   
634        NaN                                                NaN       NaN   
773      recap                                                yes       NaN   
779      recap                                                yes       NaN   
901      recap                                            painted       NaN   
1193     recap                                            painted       NaN   
1582     recap                                            painted       NaN   
1844     recap                      

<a id='outstanding1'></a>

Some of these values are reasonable, but there are few for which we will need to go back to the field notes in 2011.  Those rows in which rtl > tl need to be investigated.

[Back to Outstanding Problems](#outstanding)

In [51]:
idx_rtltlbig = (idx_dfabove50)&(df.rtl.astype(int,errors = 'ignore')>df.tl.astype(int,errors ='ignore'))
df.loc[idx_rtltlbig]

species               toes sex                 date  svl  tl rtl  \
1867      sj       b 1 - 7 - 11   F  2011-06-20 00:00:00  7.5  70  90   
1873      sj  b 2 - 9 - 15 - 17   F  2011-06-20 00:00:00  7.6  68  86   

      autotomized mass                      location meters new.recap painted  \
1867          NaN    0  3m right side ^ Juniper Xing    118     recap     yes   
1873          NaN    0            10m up CCC on slab    250     recap     yes   

      sighting paint.mark vial  \
1867       NaN        NaN  NaN   
1873       NaN       g19b  NaN   

                                                   misc  
1867  Break at 50, tail still attached w48c -> g18b ...  
1873                                                NaN

These appear to be cases where svl,tl,rtl and mass may have been entered into the wrong columns, i.e. the correct placement of current values-->correct column should probably be:
- svl-->mass
- tl-->svl
- rtl-->tl
- mass-->rtl

We will correct these now.

In [52]:
import copy
def swap(df):
    tmp = {
        'rtl':copy.copy(df['rtl']),
        'tl':copy.copy(df['tl']),
        'svl':copy.copy(df['svl']),
        'mass':copy.copy(df['mass'])
    }
#     print(tmp)
    df['rtl'] = tmp['mass']
    df['tl'] = tmp['rtl']
    df['svl'] = tmp['tl']
    df['mass'] = tmp['svl']
#     print(tmp)
    return df


In [53]:
df.loc[idx_rtltlbig,['svl','rtl','tl','mass']] = swap(df.loc[idx_rtltlbig,['svl','rtl','tl','mass']])
df.loc[idx_rtltlbig,:]

species               toes sex                 date svl  tl rtl  \
1867      sj       b 1 - 7 - 11   F  2011-06-20 00:00:00  70  90   0   
1873      sj  b 2 - 9 - 15 - 17   F  2011-06-20 00:00:00  68  86   0   

      autotomized mass                      location meters new.recap painted  \
1867          NaN  7.5  3m right side ^ Juniper Xing    118     recap     yes   
1873          NaN  7.6            10m up CCC on slab    250     recap     yes   

      sighting paint.mark vial  \
1867       NaN        NaN  NaN   
1873       NaN       g19b  NaN   

                                                   misc  
1867  Break at 50, tail still attached w48c -> g18b ...  
1873                                                NaN

Now we force rtl to int type, ignoring errors.

In [54]:
df['rtl'] = df.rtl.astype(int,errors = 'ignore')

<a id='tl'></a>

## 'tl' 
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

Here we investigate and clean values in the column 'tl'. These should be int type values that are positive.  First, we test to see if all of the values are of type int.

In [55]:
df.tl.astype(int,errors='ignore').apply(lambda x: type(x)).value_counts(dropna=False)

<class 'float'>    3590
<class 'str'>      2709
Name: tl, dtype: int64

Let us inspect the entries for which attempting to convert 'tl' results in a float type.

In [56]:
idx_floatNaNtl = df.tl.astype(int,errors='ignore').apply(lambda x: type(x) is float)
df.loc[idx_floatNaNtl,'tl'].value_counts(dropna=False)

NaN    3590
Name: tl, dtype: int64

These are all NaN entries and can be ignored for the time being.

Let's inspect the non NaN entries now.

In [57]:
idx_strtl = df.tl.astype(int,errors='ignore').apply(lambda x: type(x) is str)
df.loc[idx_strtl,'tl'].value_counts(dropna=False)

70         79
73         70
68         69
75         69
69         68
65         62
72         60
71         57
78         55
66         55
67         54
63         52
76         50
60         48
74         47
85         45
90         44
64         44
80         43
61         42
100        41
88         40
79         38
55         37
62         36
57         35
59         35
52         34
86         34
50         33
93         33
58         32
98         30
53         30
91         30
102        29
54         29
81         29
89         28
77         28
47         27
87         26
95         26
82         25
84         25
99         25
97         25
46         24
103        24
92         24
49         24
83         24
51         24
94         23
40         23
101        22
56         22
48         21
96         20
105        19
45         19
43         19
106        19
104        18
35         16
110        15
120        15
109        14
44         13
111        13
42         13
112   

With the exception of the value '56 (42)', the tl values that are not NaN could be converted to int types.  Let's inspect this entry.

In [58]:
pd.set_option('max_colwidth',1000)
idx_5642tl = df.loc[(idx_strtl) & (df.tl=='56 (42)'),:].index
df.loc[df.index.isin(idx_5642tl)]

species       toes sex                 date svl       tl rtl  \
4111      sj  1-2-3-4-5   f  2009-07-13 00:00:00  69  56 (42)  -1   

      autotomized mass                       location meters new.recap  \
4111          NaN  9.2  T opp mid wall v juniper xing     85      new    

      painted  sighting paint.mark vial  \
4111  painted       NaN        y7a  NaN   

                                                         misc  
4111  missing LFF (left front foot); open break in tail at 42

Based on the notes in the misc column, tl should be recorded as 56.  We will do this now.

In [59]:
df.loc[df.index.isin(idx_5642tl),'tl']='56'

Now the entry looks like this.

In [60]:
df.loc[df.index.isin(idx_5642tl),:]

species       toes sex                 date svl  tl rtl  autotomized  \
4111      sj  1-2-3-4-5   f  2009-07-13 00:00:00  69  56  -1          NaN   

     mass                       location meters new.recap  painted  sighting  \
4111  9.2  T opp mid wall v juniper xing     85      new   painted       NaN   

     paint.mark vial                                                     misc  
4111        y7a  NaN  missing LFF (left front foot); open break in tail at 42

We will use a histogram to try and identify abnormalities among the other tl values.

In [61]:
# dfnobadtypes0neg1 = (~df.tl.isin(badtypes))&(~df.tl.isin(['0','-1']))
dfother = ~(df.species.dropna().str.contains('v|j'))&(df.species.notna())&(df.tl.notna())
jarrovii = go.Histogram(x = df.loc[(df.species.str.contains('j'))&(df.tl.notna())
                                   ,'tl'].astype(int, 'ignore'),name = 'S. jarrovii',xbins =dict(size=1)
                        #,histnorm='probability'
                        , cumulative=dict(enabled = False, direction = 'increasing'))
virgatus = go.Histogram(x = df.loc[(df.species.str.contains('v'))&(df.tl.notna())
                                   ,'tl'].astype(int, 'ignore'), name = 'S. virgatus',xbins =dict(size=1)
                       #,histnorm='probability'
                        , cumulative=dict(enabled = False, direction = 'increasing'))
other = go.Histogram(x = df.loc[dfother,'tl'].astype(int, 'ignore'), name = 'other',xbins =dict(size=1)
                                  #,histnorm='probability'
                     , cumulative=dict(enabled = False
                                                                           , direction = 'increasing'))
data = [jarrovii, virgatus, other]
layout = go.Layout(
    title = 'Histogram of tl by species',
    titlefont = dict(
        size = 20),
    xaxis = dict(
        dtick = 1,
        title = 'tl (mm)',
#         tickfont = dict(
#         size = 8),
#         tickangle = 85,
        titlefont = dict(
            size = 18)),
    yaxis = dict(
        title = 'Number of Lizards',
        titlefont = dict(
            size = 18))
)
fig = go.Figure(
        data = data,
        layout = layout)
py.iplot(fig, filename = 'Histogram of tl by species (new)')

For now there is not much we can identify graphically.  We will revist this later.  For now we will force tl to int.

In [62]:
df['tl'] = df.tl.astype(int, errors = 'ignore')

<a id='svl'></a>

## 'svl' 
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)



We will take a similar approach for svl.

In [63]:
df.svl.astype(int,errors='ignore').apply(lambda x: type(x)).value_counts(dropna=False)

<class 'float'>    3584
<class 'str'>      2715
Name: svl, dtype: int64

Let us inspect the entries for which attempting to convert 'svl' results in a float type.

In [64]:
idx_floatNaNsvl = df.svl.astype(int,errors='ignore').apply(lambda x: type(x) is float)
df.loc[idx_floatNaNsvl,'svl'].value_counts(dropna=False)

NaN    3584
Name: svl, dtype: int64

These are all NaN entries and can be ignored for the time being.

Let's inspect the non NaN entries now.

In [65]:
idx_strsvl = df.svl.astype(int,errors='ignore').apply(lambda x: type(x) is str)
df.loc[idx_strsvl,'svl'].value_counts(dropna=False)

50       108
52        85
53        82
56        81
55        80
51        77
49        75
60        74
48        74
75        71
70        71
54        70
58        61
47        60
65        60
61        58
46        57
57        52
45        51
73        50
63        50
68        49
72        47
76        46
59        45
62        44
66        44
80        43
64        43
78        40
43        38
82        37
74        36
40        36
77        35
42        35
71        34
69        33
67        32
85        31
44        30
79        30
81        28
84        26
83        26
39        26
38        23
87        23
89        21
36        20
35        20
32        20
41        20
37        20
31        20
86        19
34        19
88        18
90        16
33        14
30        13
91        12
93         8
29         7
92         7
28         6
large      4
27         4
98         2
26         2
96         2
22         2
13         2
95         2
105        2
24         1
112        1

The values 'large', 'small', and '~70' require closer inspection.

In [66]:
idx_txtvals = df.svl.isin(['small','large','~70'])
df.loc[idx_txtvals]

species       toes  sex                 date    svl   tl  rtl  \
2027      sj  2-6-13-20    f  2001-03-23 00:00:00    ~70  NaN  NaN   
4642      sj        NaN    m  2002-03-16 00:00:00  large  NaN  NaN   
4814      sj        NaN  NaN  2002-03-17 00:00:00  large  NaN  NaN   
5175      sj        NaN    f  2002-03-20 00:00:00  large  NaN  NaN   
5640      sj        NaN    m  2002-03-19 00:00:00  large  NaN  NaN   
5784      sv        NaN    ?  2002-03-19 00:00:00  small  NaN  NaN   

      autotomized mass                                     location meters  \
2027          NaN  NaN                   bottom R wall v cave trail     30   
4642          NaN  NaN  active in crevice in wall 3m v juniper xing    112   
4814          NaN  NaN                                          H4a    194   
5175          NaN  NaN                           L across from wall    318   
5640          NaN  NaN                            up rt wall @ pool    NaN   
5784          NaN  NaN                                sb 4m ^ flatR    NaN   

     new.recap painted  sighting paint.mark  \
2027  sighting     NaN       NaN          ?   
4642  sighting     NaN       NaN          ?   
4814  sighting     NaN       NaN     w85a??   
5175  sighting     NaN       NaN       w||t   
5640  sighting     NaN       NaN        ???   
5784  sighting     NaN       NaN        NaN   

                                                                                                                                                                                          vial  \
2027  could read toes 6,13 for certain; toe 2 uncertain and didn't see 20 but this is the only right-sized female who could possible fit! Originally caught in July 1998, sb 20m ^ cave trail.   
4642                                                                                                                                                                                       NaN   
4814                                                                                                                                                                                       NaN   
5175                                                                                                                                                                                       NaN   
5640                                                                                                                                                                                       NaN   
5784                                                                                                                                                                                       NaN   

                                          misc  
2027                                       NaN  
4642                                       NaN  
4814  probably w85a but could only see the "5"  
5175                                       NaN  
5640            ~25mm original T; rest regrown  
5784                   had moth so didn'tcatch

All of these values for svl should be set to NaN since these are estimates, not measured values.  For the entry with the svl value of '~70', we can add the estimated value to the misc column. We will use the [appendstr](#appendstr) function here again.

In [67]:
idx_apprx70svl = (idx_txtvals)&(df.svl=='~70')
df.loc[idx_apprx70svl,'misc'] = df.loc[idx_apprx70svl,'misc'].apply(lambda x: appendstr(x,connector=';'
                                                        ,position='end'
                                                        ,value='svl extimated to be ~70mm'))
df.loc[idx_apprx70svl,:]

species       toes sex                 date  svl   tl  rtl  autotomized  \
2027      sj  2-6-13-20   f  2001-03-23 00:00:00  ~70  NaN  NaN          NaN   

     mass                    location meters new.recap painted  sighting  \
2027  NaN  bottom R wall v cave trail     30  sighting     NaN       NaN   

     paint.mark  \
2027          ?   

                                                                                                                                                                                          vial  \
2027  could read toes 6,13 for certain; toe 2 uncertain and didn't see 20 but this is the only right-sized female who could possible fit! Originally caught in July 1998, sb 20m ^ cave trail.   

                           misc  
2027  svl extimated to be ~70mm

In [68]:
df.loc[idx_txtvals,'svl']=np.nan
df.loc[idx_txtvals]

species       toes  sex                 date  svl   tl  rtl  autotomized  \
2027      sj  2-6-13-20    f  2001-03-23 00:00:00  NaN  NaN  NaN          NaN   
4642      sj        NaN    m  2002-03-16 00:00:00  NaN  NaN  NaN          NaN   
4814      sj        NaN  NaN  2002-03-17 00:00:00  NaN  NaN  NaN          NaN   
5175      sj        NaN    f  2002-03-20 00:00:00  NaN  NaN  NaN          NaN   
5640      sj        NaN    m  2002-03-19 00:00:00  NaN  NaN  NaN          NaN   
5784      sv        NaN    ?  2002-03-19 00:00:00  NaN  NaN  NaN          NaN   

     mass                                     location meters new.recap  \
2027  NaN                   bottom R wall v cave trail     30  sighting   
4642  NaN  active in crevice in wall 3m v juniper xing    112  sighting   
4814  NaN                                          H4a    194  sighting   
5175  NaN                           L across from wall    318  sighting   
5640  NaN                            up rt wall @ pool    NaN  sighting   
5784  NaN                                sb 4m ^ flatR    NaN  sighting   

     painted  sighting paint.mark  \
2027     NaN       NaN          ?   
4642     NaN       NaN          ?   
4814     NaN       NaN     w85a??   
5175     NaN       NaN       w||t   
5640     NaN       NaN        ???   
5784     NaN       NaN        NaN   

                                                                                                                                                                                          vial  \
2027  could read toes 6,13 for certain; toe 2 uncertain and didn't see 20 but this is the only right-sized female who could possible fit! Originally caught in July 1998, sb 20m ^ cave trail.   
4642                                                                                                                                                                                       NaN   
4814                                                                                                                                                                                       NaN   
5175                                                                                                                                                                                       NaN   
5640                                                                                                                                                                                       NaN   
5784                                                                                                                                                                                       NaN   

                                          misc  
2027                 svl extimated to be ~70mm  
4642                                       NaN  
4814  probably w85a but could only see the "5"  
5175                                       NaN  
5640            ~25mm original T; rest regrown  
5784                   had moth so didn'tcatch

Now we force the remaining svl values to int type.

In [69]:
df['svl'] = df.svl.astype(int, errors= 'ignore')

<a id='autotomized'></a>

### 'autotomized' 
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

[creating 'rtl_orig'and relabeling 'rtl' and 'autotomized](#rtlRTL_ORIGautotomized)
- [copy the values in rtl to a new column, *rtl_orig*](#copyrtl)
- [relabel entries in the autotomized column based on the values in the rtl_orig column](#relabelaut) 
- [relabel entries in the rtl column](#relabelrtl)

Here we populate the 'autotomized' column based on the values in 'rtl'.  Most of the source files did not have this category and have NaN values others have float values of 1.0, 2.0 or 3.0 for intact, autotomized with no regrowth or autotomized with regrowth, respectively.  The cleaned data for autotomized will contain  bool type values True, for having experienced auttomy (irrespective of regrowth) and False for having no evidence of havign experienced autotomy.

In [70]:
df.autotomized.value_counts(dropna=False)

NaN     6212
 1.0      61
 3.0      17
 2.0       9
Name: autotomized, dtype: int64

We will inspect the rtl values for entries with non NaN values for autotomized to determine if we can depend on rtl values to determine autotomy status.  In order to rely on rtl values, the following conditions must be met:
- all entries in which autotomized equals 1.0 must have 0 for rtl
- all entries in which autotomized equals 2.0 or 3.0 must have -1 or some value >0 for rtl

In [71]:
intact = df.loc[(df.autotomized==1),'rtl'].astype(int,errors = 'ignore').value_counts(dropna=False)
values2check = [x for x in intact.index[intact.index!=0]]
if len(values2check)>0:
    print("The rtl values associated with {} need a closer look.".format(values2check))
else:
    print("Values for 'intact' entries are as expected.  Continue.")
pd.set_option('max_colwidth',1000)
# df.loc[(df.autotomized==1)&(df.rtl.isin(['21'])),:]
df.loc[(df.autotomized==1)&(df.rtl.astype(int, errors = 'ignore').isin([str(x) for x in values2check])),:]
# need to see what broke this line

The rtl values associated with [21] need a closer look.


species       toes sex      date svl  tl rtl  autotomized mass  \
29      sv  3-7-11-16   f  19vi2010  60  42  21          1.0  8.5   

                               location meters new.recap painted  sighting  \
29  6m^bottom site on R ^fallen T in sb    -14       NEW     yes       NaN   

   paint.mark      vial    misc  
29        y1a  CA-01-cc  gravid

<a id ='outstanding2'></a>

[Back to Outstanding Problems](#outstanding)

This lizard appears to have been misrecorded and should be listed as autotomized given the amount of regrowth. This should be confirmed in the field notes. If we trust the data as recorded and depend on the rtl values to label autotomized this will be corrected, so for now we will leave this as is.

In [72]:
autotomized = df.loc[(df.autotomized==2),'rtl'].value_counts(dropna=False)
aut_values2check = [x for x in autotomized.index[autotomized.index!='-1']]# change to 'isin' aregument with 0 and -1
if len(aut_values2check)>0:
    print("{} values associated with an rtl value of {} need a closer look."\
          .format(df.loc[(df.autotomized==2)&(df.rtl.isin(aut_values2check)),:].shape[0],aut_values2check))
else:
    print("Values for 'autotomized' entries are as expected.  Continue.")
pd.set_option('max_colwidth',1000)
idx_aut_entries2check = (df.autotomized==2)&(df.rtl.isin([str(x) for x in aut_values2check]))
df.loc[idx_aut_entries2check,:]

8 values associated with an rtl value of ['0'] need a closer look.


species             toes sex        date svl   tl rtl  autotomized  mass  \
5       sj        3-6-15-17   m  18viii2010  52   70   0          2.0   4.5   
20      sj        3-6-12-18   f   26vii2010  66   79   0          2.0     9   
26      sj        3-6-13-20   f   5viii2010  48   69   0          2.0   3.5   
53      sj  3-10-13-(14)-16   m    12vi2010  92  112   0          2.0    18   
77      sj    4-7-8-9-11-18   m   26vii2010  96   97   0          2.0  24.5   
80      sj    3-10-13-14-16   m   26vii2010  91  111   0          2.0  18.5   
83      sj              NaN   f   5viii2010  70   86   0          2.0    11   
85      sv        3-8-12-16   m    20vi2010  52   58   0          2.0   3.5   

                                        location meters new.recap painted  \
5                              r outcrop ^ oak R    425       new     yes   
20                           339m; rt side 1m up    339       NEW     yes   
26                                     5m up ccc    NaN       new     yes   
53           talus^Rwall v talus left side 4m up    NaN     recap     yes   
77                              2m left of stump    364     recap     yes   
80                 1m v top R wall v talus in sb    320     recap     yes   
83                                   bottom site    NaN     recap     NaN   
85  5m v wall v wall v juniper xing left side sb     80     recap     yes   

    sighting paint.mark      vial  \
5        NaN       y68c  67-10-cc   
20       NaN       y54c  48-10-cc   
26       NaN         >c  59-10-cc   
53       NaN        w1c       NaN   
77       NaN       y51c       NaN   
80       NaN       y55c       NaN   
83       NaN     y61c.t       NaN   
85       NaN        y6a       NaN   

                                                                                                                                                               misc  
5                                                                                                                                                               Tss  
20                                                                                                                                                              Bss  
26                                                                                                                                                              NaN  
53       toe 14 looks like natural toe loss; skinny [pics], spine visible [pics], old puncture wounds on back [pics], possible injury of back rt leg at knee [pics]  
77                                                                                                         old mark wXc still visible; not the same as wXc at chute  
80  1m v top R wall in sb; last mark still visible; injuries to dorsum [pics]; toe 14 may be natural toe loss; lizard is skinny: spine and hip bones visible [pics]  
83                                                                                                                            BSS; toe 19 could be natural toe loss  
85                                                                                                                                                              NaN

<a id = 'outstanding3'></a>

[Back to Outstanding Problems](#outstanding)

Some of these cases are very straight forward given that the ratio of svl to tl is very close to 1, but others would be worth checking the original data to confirm. Another option is to use the svl to tl ratio of animals that we are sure are intact to decide how to classify these.  For now we will trust the system of recording used in 2010 and update the rtl values to '-1'.

In [73]:
df.loc[idx_aut_entries2check,'rtl'] = '-1'

In [74]:
df.loc[idx_aut_entries2check]

species             toes sex        date svl   tl rtl  autotomized  mass  \
5       sj        3-6-15-17   m  18viii2010  52   70  -1          2.0   4.5   
20      sj        3-6-12-18   f   26vii2010  66   79  -1          2.0     9   
26      sj        3-6-13-20   f   5viii2010  48   69  -1          2.0   3.5   
53      sj  3-10-13-(14)-16   m    12vi2010  92  112  -1          2.0    18   
77      sj    4-7-8-9-11-18   m   26vii2010  96   97  -1          2.0  24.5   
80      sj    3-10-13-14-16   m   26vii2010  91  111  -1          2.0  18.5   
83      sj              NaN   f   5viii2010  70   86  -1          2.0    11   
85      sv        3-8-12-16   m    20vi2010  52   58  -1          2.0   3.5   

                                        location meters new.recap painted  \
5                              r outcrop ^ oak R    425       new     yes   
20                           339m; rt side 1m up    339       NEW     yes   
26                                     5m up ccc    NaN       new     yes   
53           talus^Rwall v talus left side 4m up    NaN     recap     yes   
77                              2m left of stump    364     recap     yes   
80                 1m v top R wall v talus in sb    320     recap     yes   
83                                   bottom site    NaN     recap     NaN   
85  5m v wall v wall v juniper xing left side sb     80     recap     yes   

    sighting paint.mark      vial  \
5        NaN       y68c  67-10-cc   
20       NaN       y54c  48-10-cc   
26       NaN         >c  59-10-cc   
53       NaN        w1c       NaN   
77       NaN       y51c       NaN   
80       NaN       y55c       NaN   
83       NaN     y61c.t       NaN   
85       NaN        y6a       NaN   

                                                                                                                                                               misc  
5                                                                                                                                                               Tss  
20                                                                                                                                                              Bss  
26                                                                                                                                                              NaN  
53       toe 14 looks like natural toe loss; skinny [pics], spine visible [pics], old puncture wounds on back [pics], possible injury of back rt leg at knee [pics]  
77                                                                                                         old mark wXc still visible; not the same as wXc at chute  
80  1m v top R wall in sb; last mark still visible; injuries to dorsum [pics]; toe 14 may be natural toe loss; lizard is skinny: spine and hip bones visible [pics]  
83                                                                                                                            BSS; toe 19 could be natural toe loss  
85                                                                                                                                                              NaN

In [75]:
regrown = df.loc[(df.autotomized==3),'rtl'].value_counts(dropna=False).reset_index()['index']\
.astype(int, errors = 'ignore')
values2check = [x for x in regrown<=0]
if sum(values2check)>0:
    print("The values associated with {} need a closer look.".format(values2check))
else:
    print("Values for 'regrown' entries are as expected.  Continue.")
pd.set_option('max_colwidth',1000)
df.loc[(df.autotomized==3)&(df.rtl.isin([str(x) for x in values2check])),:]

Values for 'regrown' entries are as expected.  Continue.


Empty DataFrame
Columns: [species, toes, sex, date, svl, tl, rtl, autotomized, mass, location, meters, new.recap, painted, sighting, paint.mark, vial, misc]
Index: []

The entries labeled as a 3.0 in the autotomized column do not appear as though their rtl values will present an issue for calculating new autotomized values.  We will leave these as they are.

<a id='rtlRTL_ORIGautotomized'></a>

### creating 'rtl_orig' and relabeling 'rtl' and 'autotomized'
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColByCol)

[Back to: 'autotomized'](#autotomized)

Now we will:
- [copy the values in rtl to a new column, *rtl_orig*](#copyrtl)
- [relabel entries in the autotomized column based on the values in the rtl_orig column](#relabelaut) 
- [relabel entries in the rtl column](#relabelrtl)

<a id='copyrtl'></a>

#### copy the values in rtl to a new column, *rtl_orig*
[Back to: 'autotomized'](#autotomized)

In [76]:
df['rtl_orig'] = df.rtl

<a id='relabelaut'></a>

#### relabel entries in the autotomized column based on the values in the rtl_orig column
[Back to: 'autotomized'](#autotomized)

We will do this using the following logic:
    - if rtl_orig !=0 & rtl_orig.notna(), autotomized = True
    - if rtl_orig ==0, automized = False
    - if rtl_orig.isna(), autotomized = np.nan

In [77]:
idx_auttrue = (~df.rtl_orig.isin(['0']))&(df.rtl_orig.notna())
df.loc[idx_auttrue,'autotomized'] = True

In [78]:
idx_autfalse = (df.rtl_orig.isin(['0']))&(df.rtl_orig.notna())
df.loc[idx_autfalse,'autotomized'] = False

In [79]:
idx_autnan = df.rtl_orig.isna()
df.loc[idx_autnan,'autotomized'] = np.nan

<a id='relabelrtl'></a>

#### relabel entries in the rtl column
[Back to: 'autotomized'](#autotomized)
We will do this using the following logic:
    - if rtl_orig == -1, rtl = 0

In [80]:
idx_rtlneg1 = df.rtl_orig=='-1'
df.loc[idx_rtlneg1,'rtl'] = 0

In [81]:
df.autotomized.value_counts(dropna=False)

NaN      3591
False    1989
True      719
Name: autotomized, dtype: int64

<a id = 'toes'></a>

## toes 
[Top](#TOC)

[Top Cleaning](#CleaningData)

Here we make changes to toes based on comments regarding a 2004 male Sv with toes recorded as '1-6-16-17-20'

In [82]:
idx_sv2004m16161720 = (df.species=='sv') \
& (df.sex=='m') \
& (df.date.str.contains('2004-07-04')) \
&(df.svl=='52')&(df.tl=='53')

df.loc[idx_sv2004m16161720]

species          toes sex                 date svl  tl  rtl autotomized  \
5907      sv  1-6-16-17-20   m  2004-07-04 00:00:00  52  53  NaN         NaN   

     mass      location meters new.recap  painted  sighting paint.mark vial  \
5907  3.6  bottom chute    355     recap  painted       NaN        w.t  NaN   

           misc rtl_orig  
5907  few mites      NaN

In [83]:
df.loc[idx_sv2004m16161720,'toes'] = '1-7-16-17-20'
df.loc[idx_sv2004m16161720,'rtl'] = 0

Now this entry looks like this.

In [84]:
df.loc[idx_sv2004m16161720]

species          toes sex                 date svl  tl rtl autotomized  \
5907      sv  1-7-16-17-20   m  2004-07-04 00:00:00  52  53   0         NaN   

     mass      location meters new.recap  painted  sighting paint.mark vial  \
5907  3.6  bottom chute    355     recap  painted       NaN        w.t  NaN   

           misc rtl_orig  
5907  few mites      NaN

First we will rename "toes" to "toes_orig"

In [85]:
df = df.rename(columns = {'toes':'toes_orig'},index = str)

Next we create a new column, "toes"  for the renamed toes

In [86]:
df['toes'] = df.toes_orig

Now we attempt to identify problem toes name and correct or export for review.

In [87]:
pattern1 = ".( {1,}-.|.- {1,}.)" # toes entries with any number of spaces on either side of a hyphen
pattern2 = ".( {,}\w{,} {1,})." # toes entries with space around or between numbers <- the spaces here should be deleted
pattern3 = ".(')."
pattern4 = "./."  # entries with '/' <-- need to replace these with '-'
pattern5 = "(\?{1,})"#<-- these needs to be investigated
pattern6 = "^\d{3,}$" # entries consist of only a single number comprised of at least three digits 
#<-- these needs to be investigated by checking raw field notes
pattern7 = ".(-{2,})." # entries which have at least 2 consecutive '-' <- these should be investigated
pattern8 = "^0" # entries in which single digit numbers have a leading "0" <-- Check raw field notes on this too
pattern9 = "a\w" #<--handled hyphens should be inserted  between the [ab] and \w 
# entries that contain an 'a' or 'b' followed by any character in the set [a-zA-Z0-9_]
pattern10 = "b\w" #<--handled hyphens should be inserted  between the [ab] and \w 
pattern11 = "\wa" # entries that contain an 'a' or 'b' preceded by any character in the set [a-zA-Z0-9_]
pattern12 = "\wb" # entries that contain an 'a' or 'b' preceded by any character in the set [a-zA-Z0-9_]
pattern13 = "[()]"
# remove space before 'a' at end of toes
#investigate '\d-', 
#'-(*)-', 
#' (16) ', 
#'---', <- may not exist in raw data
#'\d- ', 
#'- \d', 
#transcription errors from excel (toes in date format,
#'-\d\d\d\d' <- may not be in the data set

We'll have to change this block if we add or remove toe patterns.
This is not ideal and needs to be fixed

In [88]:
toe_pattern = pd.Series([*range(1,14)]) 
toe_pattern = make_str(toe_pattern)
print(toe_pattern)

toe_pattern_descr = pd.Series([pattern1,pattern2,pattern3,pattern4
                               ,pattern5,pattern6,pattern7,pattern8
                               ,pattern9,pattern10,pattern11,pattern12,pattern13])
toe_pattern_descr = toe_pattern_descr.astype(str)
print(toe_pattern_descr)

toe_pattern_reference = pd.DataFrame({'toe_pattern': toe_pattern,'description':toe_pattern_descr})
toe_pattern_reference

0     01
1     02
2     03
3     04
4     05
5     06
6     07
7     08
8     09
9     10
10    11
11    12
12    13
dtype: object
0     .( {1,}-.|.- {1,}.)
1      .( {,}\w{,} {1,}).
2                   .(').
3                     ./.
4                (\?{1,})
5                ^\d{3,}$
6               .(-{2,}).
7                      ^0
8                     a\w
9                     b\w
10                    \wa
11                    \wb
12                   [()]
dtype: object


toe_pattern          description
0           01  .( {1,}-.|.- {1,}.)
1           02   .( {,}\w{,} {1,}).
2           03                .(').
3           04                  ./.
4           05             (\?{1,})
5           06             ^\d{3,}$
6           07            .(-{2,}).
7           08                   ^0
8           09                  a\w
9           10                  b\w
10          11                  \wa
11          12                  \wb
12          13                 [()]

We first replace the string 'nan' with a null value

In [89]:
df.loc[df.toes=='nan','toes'] = np.nan

Let's see how many of these patterns we need to correct

In [90]:
df['toe_pattern'] = np.nan

Here we use a for-loop to label the patterns 
(there's probably a better way to do this with pandas map or apply, but I'll have to figure this out, for now this is fast enough, but it could make a difference with a larger data set or with more patterns)

In [91]:
for i in range(0,toe_pattern_reference.shape[0]):
    tmp_pat_num = toe_pattern_reference.iloc[i,0]
    tmp_pattern = toe_pattern_reference.iloc[i,1]
    df = label_pattern(df,tmp_pat_num,tmp_pattern,'toe_pattern','toes')

A quick summary of the number of observations for each pattern in the data set

In [92]:
toe_errors =df.toe_pattern.value_counts(dropna=False).reset_index()\
.rename(columns = {'index':'toe_pattern','toe_pattern':'observations'})
toe_errors.loc[toe_errors.toe_pattern.isnull(),'toe_pattern'] = 'Not covered by current patterns'
toe_errors_desc = toe_errors.merge(toe_pattern_reference,'left',on='toe_pattern')
toe_errors_desc

toe_pattern  observations          description
0  Not covered by current patterns          5998                  NaN
1                               02           258   .( {,}\w{,} {1,}).
2                               01            39  .( {1,}-.|.- {1,}.)
3                               05             2             (\?{1,})
4                               09             1                  a\w
5                               13             1                 [()]

Now let's make sure we've accounted for every row in the data set

In [93]:
accountedRows = toe_errors.observations.sum()
totalRows = df.shape[0]
notAccountedRows = df.shape[0] - toe_errors.observations.sum()
print("\nThere are {} rows accounted for in the patterns (including null values) and there {} rows in the full data set.\
  There are {} rows unaccounted for.".format(accountedRows,totalRows,notAccountedRows))


There are 6299 rows accounted for in the patterns (including null values) and there 6299 rows in the full data set.  There are 0 rows unaccounted for.


Now we correct these patterns. We'll preserve the original toe data in a column called "toes_orig" just in case.  We can drop this later, if we are comfortable with the changes.  The new toes will be labeled "toes".

In [94]:
corrections_config = {'01':{'action':'replace','pattern_b':" ",'replacement':"\"\""},
            '02':{'action':'replace','pattern_b':" ",'replacement':"-"},
            '03':{'action':'replace','pattern_b':"\'",'replacement':"\"\""},
            '04':{'action':'replace','pattern_b':"/",'replacement':"-"},
            '05':{'action':'save','pattern_b':np.nan,'replacement':np.nan},
            '06':{'action':'save','pattern_b':np.nan,'replacement':np.nan},
            '07':{'action':'save','pattern_b':np.nan,'replacement':np.nan},
            '08':{'action':'replace','pattern_b':"^0",'replacement':"\"\""},
            '09':{'action':'replace','pattern_b':'a','replacement':'-a'},
            '10':{'action':'replace','pattern_b':'b','replacement':'-b'},          
            '11':{'action':'replace','pattern_b':"a",'replacement':"a-"},
            '12':{'action':'replace','pattern_b':"b",'replacement':"b-"},
            '13':{'action':'replace','pattern_b':"[()]",'replacement':"\"\""}}

In [95]:
toe_errors_desc['action'] = toe_errors_desc.loc[toe_errors_desc.toe_pattern.str.len()==2].toe_pattern\
.map(lambda x: corrections_config[x]['action'],na_action='ignore')

toe_errors_desc['replacement'] = toe_errors_desc.loc[toe_errors_desc.toe_pattern.str.len()==2].toe_pattern\
.map(lambda x: corrections_config[x]['replacement'],na_action='ignore')

toe_errors_desc = toe_errors_desc.sort_values('toe_pattern').reset_index(drop=True)
toe_errors_desc

toe_pattern  observations          description  \
0                               01            39  .( {1,}-.|.- {1,}.)   
1                               02           258   .( {,}\w{,} {1,}).   
2                               05             2             (\?{1,})   
3                               09             1                  a\w   
4                               13             1                 [()]   
5  Not covered by current patterns          5998                  NaN   

    action replacement  
0  replace          ""  
1  replace           -  
2     save         NaN  
3  replace          -a  
4  replace          ""  
5      NaN         NaN

In [96]:
for i in range(0,toe_errors_desc.shape[0]):
    tmp_pat_num = toe_errors_desc.iloc[i,0]
    tmp_pattern = toe_errors_desc.iloc[i,2]
    action = toe_errors_desc.iloc[i,3]
    tmp_replacement = toe_errors_desc.iloc[i,4]
    tmp_x = df.loc[df.toe_pattern==tmp_pat_num,:]
    
    if action =='save':
        tmp_filename = 'pattern'+tmp_pat_num+'.csv'
        tmp_x.to_csv(tmp_filename)
        print("Pattern {} successfully saved to {}.".format(tmp_pattern,tmp_filename))
    if action =='replace':
        df.loc[df.toe_pattern==tmp_pat_num,'toes'] = replace_pattern(x=df.loc[df.toe_pattern==tmp_pat_num]
                                                                     ,pattern = tmp_pat_num
                                                                     ,pattern_b = tmp_pattern
                                                                     ,source_col = 'toes'
                                                                    ,replacement = tmp_replacement)
        print("Pattern {} successfully replaced with {}.".format(tmp_pattern,tmp_replacement))
    else:
        print("No direction provided for pattern {}.  No action was taken.".format(tmp_pattern))

Pattern .( {1,}-.|.- {1,}.) successfully replaced with "".
Pattern .( {,}\w{,} {1,}). successfully replaced with -.
Pattern (\?{1,}) successfully saved to pattern05.csv.
No direction provided for pattern (\?{1,}).  No action was taken.
Pattern a\w successfully replaced with -a.
Pattern [()] successfully replaced with "".
No direction provided for pattern nan.  No action was taken.


Now we confirm that the patterns we expect to have eliminated have indeed been eliminated from the data set

In [97]:
for i in range(0,toe_pattern_reference.shape[0]):
    tmp_pattern = str(toe_pattern_reference.iloc[i,1])
    print(report_pattern(df,tmp_pattern,'toes','Post-Correction'))

Post-Correction:
toe pattern .( {1,}-.|.- {1,}.):0
Post-Correction:
toe pattern .( {,}\w{,} {1,}).:0
Post-Correction:
toe pattern .(').:0
Post-Correction:
toe pattern ./.:0
Post-Correction:
toe pattern (\?{1,}):2
Post-Correction:
toe pattern ^\d{3,}$:0
Post-Correction:
toe pattern .(-{2,}).:0
Post-Correction:
toe pattern ^0:0
Post-Correction:
toe pattern a\w:0
Post-Correction:
toe pattern b\w:0
Post-Correction:
toe pattern \wa:0
Post-Correction:
toe pattern \wb:0
Post-Correction:
toe pattern [()]:0


This is as expected since we left toe pattern 4 uncorrected.

<a id='sex'></a>

### sex
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

Next we move on to cleaning the "sex" column.

First we want to get an idea of the types of problems in the sex column.  We start by striping leading and trailing whitespaces.  You can see here that there were none in the data set.

In [98]:
print(df.sex.str.len().unique())# returns unique lengths of sex
df.sex=df.sex.str.strip()
print(df.sex.str.len().unique())

[ 1. nan  2.  3.  4.  5.]
[ 1. nan  2.  3.  0.  4.  5.]


#### Identify non "m" or "f" values and their frequencies

In [99]:
patterns_sex="m|f|NA"
non_matches=df.sex.loc[df.sex.str.match(patterns_sex)!=True]
print("\nThere are {} entries for sex which do not match the patterns {}:"\
      .format(non_matches.shape[0],patterns_sex.split("|")))
non_matches.value_counts()


There are 3707 entries for sex which do not match the patterns ['m', 'f', 'NA']:


juv      122
F        112
M         88
?         15
?f         6
n          2
adult      1
[m]        1
?m         1
unm        1
???        1
           1
Name: sex, dtype: int64

#### Identify values to convert to NA, m, or f

In [100]:
sex2NA = ['adult','juv','nan','\?\?\?','\?']
sex2m = ['unm','M']
sex2f = ['F']
df.loc[df.sex.isin(sex2NA)==True]
print("There are {} entries that should be converted to 'NaN'".format(df.sex.isin(sex2NA).sum()))
print("There are {} entries that should be converted to 'm'".format(df.sex.isin(sex2m).sum()))
print("There are {} entries that should be converted to 'f'".format(df.sex.isin(sex2f).sum()))

There are 123 entries that should be converted to 'NaN'
There are 89 entries that should be converted to 'm'
There are 112 entries that should be converted to 'f'


#### Convert the values to NA, f, or m, respectively.

In [101]:
df.loc[df.sex.isin(sex2NA),'sex']=np.nan
df.loc[df.sex.isin(sex2m),'sex']='m'
df.loc[df.sex.isin(sex2f),'sex']='f'
print("Now there are {} entries that should be converted to 'NaN'".format(df.sex.isin(sex2NA).sum()))
print("Now there are {} entries that should be converted to 'm'".format(df.sex.isin(sex2m).sum()))
print("Now there are {} entries that should be converted to 'f'".format(df.sex.isin(sex2f).sum()))

Now there are 0 entries that should be converted to 'NaN'
Now there are 0 entries that should be converted to 'm'
Now there are 0 entries that should be converted to 'f'


#### Set all remaining sex with "?" to NaN

In [102]:
df.loc[(df.sex.str.contains('\?')) & (df.sex.notnull()),'sex'] = np.nan

<a id = 'species'></a>

### Species
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

In [103]:
print(df.species.str.len().unique())# returns unique lengths of species
df.species=df.species.str.strip()
print(df.species.str.len().unique())

[ 2.  3.  5.  1. nan  4. 30.]
[ 2.  3.  5.  1. nan 30.]


In [104]:
df.species.value_counts(dropna = False)

sj                                3494
sv                                1161
j                                  720
uo                                 226
NaN                                204
v                                  180
Sj                                 119
cn                                  59
Sv                                  52
Uo                                  27
sc                                  22
Ae                                  11
as                                   8
?                                    3
ek                                   2
??                                   2
cn ex                                2
cn2                                  1
sc?                                  1
sj?                                  1
Snake sighted at root crossing       1
c                                    1
ce                                   1
up                                   1
Name: species, dtype: int64

In [105]:
patterns_species="j|v|sj|sv|NA"
idx_notsjsv = (df.species.str.match(patterns_species)!=True)&(df.species.str.contains('j|v',case=False)!=True)
non_matches=df.species.loc[idx_notsjsv]
print("\nThere are {} entries for species which do not match the patterns {} and are unlikely to be definitely \
'sv', 'sj':".format(non_matches.shape[0],patterns_species.split("|")))
non_matches.value_counts()


There are 572 entries for species which do not match the patterns ['j', 'v', 'sj', 'sv', 'NA'] and are unlikely to be definitely 'sv', 'sj':


uo                                226
cn                                 59
Uo                                 27
sc                                 22
Ae                                 11
as                                  8
?                                   3
cn ex                               2
??                                  2
ek                                  2
Snake sighted at root crossing      1
c                                   1
up                                  1
ce                                  1
cn2                                 1
sc?                                 1
Name: species, dtype: int64

We will set species for these entries to  'other'.

In [106]:
df.loc[df.species.isin(non_matches.unique()),'species'] = 'other'

<a id ='outstanding4'></a>
#### *Sceloporus jarrovii*
[Back to Outstanding Problems](#outstanding)

In [107]:
df.loc[df.species.str.contains('j',case=False),'species'].value_counts(dropna=False)

sj     3494
j       720
Sj      119
sj?       1
Name: species, dtype: int64

The values with '?' should be investigated.

In [108]:
idx_sjrev = df.species.str.contains('j',case=False)&(df.species.str.contains('\?'))
df.loc[idx_sjrev,'species'].value_counts(dropna=False)
df.loc[idx_sjrev,:]

species toes_orig sex                 date svl  tl rtl autotomized mass  \
270     sj?   4-10-19   m  2005-07-11 00:00:00  54  61  23        True  6.8   

    location meters new.recap  painted  sighting paint.mark vial  \
270       sb    -45     recap  painted       NaN       w27a  NaN   

                                misc rtl_orig      toes toe_pattern  
270  paint almost gone --> repainted       23   4-10-19         NaN

In [109]:
idx_sj = df.species.str.contains('j',case=False)&(~df.species.str.contains('\?'))
df.loc[idx_sj,'species'].value_counts(dropna=False)

sj    3494
j      720
Sj     119
Name: species, dtype: int64

We will convert the others should be converted to 'j'.

In [110]:
df.loc[idx_sj,'species'] = 'j'

#### *Sceloporus virgatus*

In [111]:
idx_sv = df.species.str.contains('v',case=False)
df.loc[idx_sv,'species'].value_counts(dropna=False)

sv    1161
v      180
Sv      52
Name: species, dtype: int64

We will convert these to 'v'.

In [112]:
df.loc[idx_sv,'species'] = 'v'

<a id='newrecap'></a>

### new.recap
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

1. [potential new and recap](#newandrecap)

In [113]:
newKeep = ['new','n','NEW','N','New']
recapKeep = ['recap','r','Recap','R']
sighting = ['sighting','sighted','heard','sighted ', 'missed']

Now let's identify other values to include in each list.

<a id = 'newandrecap'></a>
#### potential new and recap

[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

[Back to: new.recap](#newrecap)

Let's identify cases that may be classified as recaptures or new captures.  We'll start with new captures.

In [114]:
idx_potnew = df['new.recap'].str.contains('n',case=False)==True
print([x for x in df.loc[idx_potnew,'new.recap'].value_counts(dropna=False).index])
df.loc[idx_potnew,'new.recap'].value_counts(dropna=False)

['sighting', 'NEW', 'new', 'new ', 'N', 'new?', 'recap? - toes suggest a NEW mark', '?sighting', "didn't catch", 'New', 'sighing', 'recap/new', 'not caught']


sighting                            2250
NEW                                  625
new                                  554
new                                  107
N                                     71
new?                                   3
recap? - toes suggest a NEW mark       1
?sighting                              1
didn't catch                           1
New                                    1
sighing                                1
recap/new                              1
not caught                             1
Name: new.recap, dtype: int64

'NEW', 'New', 'new ', 'new', and 'N' are certainly new captures and should be converted to 'N'. for now we will add them to the *newKeep* list.

In [115]:
newKeep = list(set(newKeep + ['NEW', 'New', 'new ', 'new', 'N']))
newKeep

['NEW', 'new ', 'new', 'New', 'N', 'n']

'sighting', '?sighting', "didn't catch", 'sighing', and 'not caught' should be sightings, so wee will add them to the list of *sighting* list now.

In [116]:
sighting = list(set(sighting + ['sighting', '?sighting', 'didn\'t catch', 'sighing', 'not caught']))
sighting

['?sighting',
 'sighted ',
 'sighting',
 'missed',
 'not caught',
 "didn't catch",
 'sighted',
 'sighing',
 'heard']

now we take a similar approach for recaptures.

In [117]:
idx_potrec = df['new.recap'].str.contains('r',case=False)==True
print([x for x in df.loc[idx_potrec,'new.recap'].value_counts(dropna=False).index])
df.loc[idx_potrec,'new.recap'].value_counts(dropna=False)

['recap', 'r', 'recap?', 'recap ', 'visual recapture', 'recap? - toes suggest a NEW mark', 'heard', 'reecap', 'recap/new', 'recapq', 'recap ?', 'r?']


recap                               1128
r                                     59
recap?                                 9
recap                                  2
visual recapture                       1
recap? - toes suggest a NEW mark       1
heard                                  1
reecap                                 1
recap/new                              1
recapq                                 1
recap ?                                1
r?                                     1
Name: new.recap, dtype: int64

'recap', 'r', 'recap ',  'reecap', 'recapq' are certainly recaptures and should be converted to 'R'. for now we will add them to the *newRecapKeep* list.

In [118]:
recapKeep = list(set(recapKeep + ['recap', 'r', 'recap ',  'reecap', 'recapq']))
recapKeep

['recap ', 'R', 'recapq', 'recap', 'r', 'Recap', 'reecap']

'recap?', 'recap/new', 'recap? - toes suggest a NEW mark','recap ?', 'r?' require inspection.

In [119]:
idx_recaprev = df['new.recap']\
.isin(['recap?','recap/new', 'recap ?', 'recap? - toes suggest a NEW mark', 'r?'])
df.loc[idx_recaprev]

species  toes_orig sex                 date  svl   tl  rtl autotomized  \
95         j  3-6-11-19   m           19viii2010  NaN  NaN  NaN         NaN   
300        j      12-13   f  2005-07-03 00:00:00   75   76   13        True   
302        j          4   m  2013-07-03 00:00:00   68   90    0       False   
304        j         16   m  2013-07-11 00:00:00   73   30   24        True   
363        v         18   m  2013-07-03 00:00:00   49   52   37        True   
500        v         14   m  2014-07-11 00:00:00   55   49    3        True   
795    other          7   f  2012-05-24 00:00:00   84  130   55        True   
796        j         14   f  2012-06-05 00:00:00   72  100    0       False   
1878       j         14   f  2011-06-21 00:00:00   58   77    0       False   
2126       j          4   f  2001-07-12 00:00:00   65   92    0       False   
2553       j     2-9-15   f  2001-08-01 00:00:00   72   97    0       False   
4076       j         12   m  2008-07-13 00:00:00   62   68   22        True   
4340       j    7-15-18   m  2016-05-22 00:00:00   80   76   23        True   

          mass  \
95         NaN   
300       12.5   
302          8   
304        8.4   
363        3.8   
500        5.1   
795   24.7-6.7   
796         12   
1878       5.2   
2126         8   
2553      12.5   
4076       8.5   
4340        16   

                                                                         location  \
95                                                     1m v bottom rt curved wall   
300                                                  wall between pool and 2falls   
302                                                       streambed bottom island   
304                                                                downed juniper   
363                                                                 R v left slab   
500                                                                  sb pyramid R   
795                                                                        CC/CCC   
796                                                          Rs rt side 3m v slab   
1878                                                                         slab   
2126                                                          R wall left S curve   
2553                                              3m up left sidewall @ 2triple R   
4076                                               16m ^ CC/CCC in CCC on rt side   
4340  R off site ~10m to right of sb at -40 (in alt sb that starts at site entry)   

     meters                         new.recap  painted  sighting paint.mark  \
95       24  recap? - toes suggest a NEW mark      yes       NaN        y:t   
300     385                            recap?  painted       NaN       w14c   
302     142                            recap?      yes       NaN        o5c   
304     220                         recap/new      yes       NaN       o46c   
363     262                            recap?      yes       NaN        o5a   
500     373                            recap?      yes       NaN       o43a   
795     NaN                            recap?      yes       NaN        wXc   
796     NaN                            recap?      yes       NaN       w48c   
1878    262                            recap?      yes       NaN       g28b   
2126    280                           recap ?      NaN       NaN       r28a   
2553    335                            recap?      NaN       NaN      r101a   
4076    256                                r?  painted       NaN        y:t   
4340     --                            recap?      yes       NaN        yXc   

                                                                                                                                                     vial  \
95                                                                                                                                                    NaN   
300                              

'visual recapture', and 'heard' should be reclassified as 'sighting', so we will add them to the *sighting* list.

In [120]:
sighting = list(set(sighting + ['visual recapture', 'heard']))
sighting

['?sighting',
 'sighted ',
 'sighting',
 'missed',
 'not caught',
 "didn't catch",
 'sighted',
 'sighing',
 'visual recapture',
 'heard']

Now we assign 'N' to confired new captures.

In [121]:
idx_new = df['new.recap'].isin(newKeep)
df.loc[idx_new,'new.recap'] = 'N'
df.loc[idx_new,'new.recap'].value_counts(dropna = False)

N    1358
Name: new.recap, dtype: int64

Now we assign 'R' to confirmed recaptures.

In [122]:
idx_recap = df['new.recap'].isin(recapKeep)
df.loc[idx_recap,'new.recap'] = 'R'
df.loc[idx_recap,'new.recap'].value_counts(dropna = False)

R    1191
Name: new.recap, dtype: int64

Now we assign 'S' to confirmed sightings.

In [123]:
idx_sighting = df['new.recap'].isin(sighting)
df.loc[idx_sighting,'new.recap'] = 'S'
df.loc[idx_sighting,'new.recap'].value_counts(dropna = False)

S    2478
Name: new.recap, dtype: int64

The remaining *new.recap* values need inspection.

In [124]:
print(df.loc[~df['new.recap'].isin(['R','N','S']),'new.recap'].unique())
idx_2check = ~df['new.recap'].isin(['R','N','S'])
df.loc[idx_2check,'new.recap'].value_counts()

['?' 'recap? - toes suggest a NEW mark' nan 'recap?' 'recap/new' 'new?'
 '???' 'collected' 'recap ?' 'Dead' 'r?']


recap?                              9
?                                   5
new?                                3
???                                 2
recap? - toes suggest a NEW mark    1
collected                           1
Dead                                1
recap/new                           1
recap ?                             1
r?                                  1
Name: new.recap, dtype: int64

In [125]:
print("There are {} entries which need to be checked and classfied."\
      .format(df.loc[(idx_2check) & (df['new.recap'].notna()) ].shape[0]))
df.loc[(idx_2check) & (df['new.recap'].notna())]

There are 25 entries which need to be checked and classfied.


species   toes_orig  sex                 date  svl   tl  rtl autotomized  \
0          j   2-6-12-15    m             19vi2010   80  110   29        True   
95         j   3-6-11-19    m           19viii2010  NaN  NaN  NaN         NaN   
300        j       12-13    f  2005-07-03 00:00:00   75   76   13        True   
302        j           4    m  2013-07-03 00:00:00   68   90    0       False   
304        j          16    m  2013-07-11 00:00:00   73   30   24        True   
363        v          18    m  2013-07-03 00:00:00   49   52   37        True   
418        j          15    f  2014-07-03 00:00:00   67   56   30        True   
500        v          14    m  2014-07-11 00:00:00   55   49    3        True   
505        j          13    f  2000-03-18 00:00:00   55   72    0       False   
713        v           2    m  2012-06-02 00:00:00   53   72    0       False   
795    other           7    f  2012-05-24 00:00:00   84  130   55        True   
796        j          14    f  2012-06-05 00:00:00   72  100    0       False   
1878       j          14    f  2011-06-21 00:00:00   58   77    0       False   
1915       j          7-    f  2001-03-19 00:00:00   55   76    0       False   
2105       j         NaN  NaN  2001-07-11 00:00:00  NaN  NaN  NaN         NaN   
2126       j           4    f  2001-07-12 00:00:00   65   92    0       False   
2553       j      2-9-15    f  2001-08-01 00:00:00   72   97    0       False   
2661       v       13-14    m  2015-07-13 00:00:00   47   38   15        True   
2801       j         NaN  NaN  2006-05-21 00:00:00  NaN  NaN  NaN         NaN   
3944       j   1-12-17 a    f  2008-07-04 00:00:00   65   91    0       False   
3945       j   1-2-3-4-5    f  2008-07-04 00:00:00   58   66   16        True   
4076       j          12    m  2008-07-13 00:00:00   62   68   22        True   
4240       j         NaN  NaN  2016-05-09 00:00:00  NaN  NaN  NaN         NaN   
4340       j     7-15-18    m  2016-05-22 00:00:00   80   76   23        True   
6253       j           7    m  2004-07-22 00:00:00   39   52    0       False   

          mass  \
0           20   
95         NaN   
300       12.5   
302          8   
304        8.4   
363        3.8   
418          8   
500        5.1   
505        5.8   
713        4.4   
795   24.7-6.7   
796         12   
1878       5.2   
1915       5.3   
2105       NaN   
2126         8   
2553      12.5   
2661       3.5   
2801       NaN   
3944       7.2   
3945       4.8   
4076       8.5   
4240       NaN   
4340        16   
6253         2   

                                                                         location  \
0                                                               10m v bottom bowl   
95                                                     1m v bottom rt curved wall   
300                                                  wall between pool and 2falls   
302                                                       streambed bottom island   
304                                                                downed juniper   
363                                                                 R v left slab   
418                                                            wall v bottom wall   
500                                                                  sb pyramid R   
505                                                       5m^wall from sb10m^slab   
713                                                           pine at top of site   
795                                                                        CC/CCC   
796                                                          Rs rt side 3m v slab   
1878                                                                         slab   
1915                                                                         slab   
2105                                                                         pool   
2126                                                          R wall 

<a id='date'></a>

### date
[Back to: Top](#TOC)

[Back to: Cleaning](#CleaningData)

[Back to: Column-by-Column Cleaning](#ColbyCol)

We need to handle the date data which don't confirm to a typical date format (e.g., 2010 data which contain roman numerals).

In [126]:
idx_romdate = (df.date.notna())&(df.date.str.contains('i|v|x'))
df.loc[idx_romdate,'date'].value_counts(dropna = False)

26vii2010     15
20vi2010      13
21vi2010      13
18viii2010    10
5viii2010     10
10vii2010      8
27vii2010      5
19vi2010       5
13viii2010     5
19viii2010     4
20vii2010      3
14viii2010     3
14vi2010       2
2viii2010      2
12vi2010       1
Name: date, dtype: int64

Now we need to replace the values in the date strings with the roma month surrounded by hyphens.

In [127]:
df.loc[idx_romdate,'date'] = df.loc[idx_romdate,'date'].apply(lambda x: rom2arab(x))
# .apply(lambda x: pd.to_datetime(rom2arab(x),errors='ignore'))
df.loc[idx_romdate,'date'].head()

0    19-06-2010
1    13-08-2010
2    18-08-2010
3    18-08-2010
4    18-08-2010
Name: date, dtype: object

This is what the replaced values look like now.

In [128]:
df.loc[~idx_romdate,'date'].head()

99     2005-07-11 00:00:00
100    2005-07-05 00:00:00
101    2005-07-06 00:00:00
102    2005-07-06 00:00:00
103    2005-07-07 00:00:00
Name: date, dtype: object

<a id= 'resumehere'></a>

[Top](#TOC)

In [129]:
df.loc[idx_romdate,'date'] = df.loc[idx_romdate].date.apply(pd.to_datetime)
# some weird stuff is happening when I try to assign these values to the object their supposed to be in
# I'll have to figure this out later. Right now this only affects 2010 data, so I'll move on
df.loc[idx_romdate,'date'].head() 

0    1276905600000000000
1    1281657600000000000
2    1282089600000000000
3    1282089600000000000
4    1282089600000000000
Name: date, dtype: object

<a id='CorrectingClass'></a>

## Correcting class of columns
[Top](#TOC)

[Top Cleaning](#CleaningData)

### Convert integer columns to int

In [130]:
intCols = ['meters']
df[intCols]=df[intCols].astype(int,errors='ignore')

### Convert numeric columns to numeric

In [131]:
numCols = ['svl','tl','rtl','mass']
df[numCols]=df[numCols].apply(pd.to_numeric,errors='coerce')

### Convert string columns to str

In [132]:
strCols = ['toes','sex','species','vial']
df[strCols]=df[strCols].astype(str, errors='ignore')

### Convert date to datetime

In [133]:
df.loc[df.date=="NA"]=np.nan
df.date = pd.to_datetime(df.date,errors='ignore')

In [134]:
print("\nAfter applying the above changes, the data types are as follows:\n{}".format(df.dtypes))


After applying the above changes, the data types are as follows:
species                object
toes_orig              object
sex                    object
date           datetime64[ns]
svl                   float64
tl                    float64
rtl                   float64
autotomized            object
mass                  float64
location               object
meters                 object
new.recap              object
painted                object
sighting              float64
paint.mark             object
vial                   object
misc                   object
rtl_orig               object
toes                   object
toe_pattern            object
dtype: object


<a id='AddVar1'></a>

## Adding variables [*year*](#year) and [*rtl_orig*](#rtlorig)

<a id='year'></a>

### Year
[Back to: Top](#TOC)

[Back to: Adding variables](#AddVar1)

We will use data contained in the *date* column to create the variable *year*.  TO do this we will define a small function, [*myint*](#myint), to convert year to an int type.

Now we apply [*myint*](#myint) to the 'date' column to create the variable year and inspect the unique values.

In [135]:
df['year'] = df.date.dt.year.apply(myint,verbose=False)
df.year.value_counts(dropna=False)

2002    1477
2003    1017
2017     759
2001     681
2004     478
2000     209
2005     202
2007     182
2006     163
2009     162
2015     147
nan      136
2008     134
2013     106
2016     101
2010      99
2014      97
2012      85
2011      64
Name: year, dtype: int64

Let's inspect the entries with 'nan' values.  Note these 'nan' values are string values and not NaN.

In [136]:
df.loc[df.year=='nan',:]

species            toes_orig  sex date   svl    tl   rtl autotomized  \
2707   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2708   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2709   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2710   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2711   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2712   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2713   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2714   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2715   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2716   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2717   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2718   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2719   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2720   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2721   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2722   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2723   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2724   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2725   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2726   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2727   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2728   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2729   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2730   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2731   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2732   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2733   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2734   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2735   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2736   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2737   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2738   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2739   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2740   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2741   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2742   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2743   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2744   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2745   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2746   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2747   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2748   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2749   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2750   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2751   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2752   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2753   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2754   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2755   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2756   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2757   other                  NaN  nan  NaT   NaN   NaN   NaN         NaN   
2

In [137]:
idx_nntoes = (df.year=='nan')&(df.toes_orig.notna())&(df.toes_orig!='nan')
print("{} of these entries have non-null values in the originl toes column.  Let's inspect these"\
      .format(df.loc[idx_nntoes].shape[0]))

6 of these entries have non-null values in the originl toes column.  Let's inspect these


In [138]:
df.loc[idx_nntoes]

species            toes_orig sex date   svl    tl   rtl autotomized  \
3905       j                 9-13   m  NaT  50.0  68.0   0.0       False   
3918       j  2017-12-16 00:00:00   f  NaT  54.0  75.0   0.0       False   
3939       j                11-18   m  NaT  48.0  63.0   0.0       False   
3940       j                 9-15   f  NaT  73.0  65.0  36.0        True   
4241       v            1-6-11-20   m  NaT  48.0  63.0   0.0       False   
4297       j              7-15-20   m  NaT  69.0  54.0  12.0        True   

      mass                         location meters new.recap    painted  \
3905   4.1                    sb 5m v trail    -35         N        yes   
3918   5.1                           CCC/CC    NaN         R  repainted   
3939   3.7           bigR in sb 3m ^ 1falls    NaN         R  repainted   
3940  11.0  bottom bowl on rt side v 1falls    NaN         N        yes   
4241   3.3                 sb 1m v 2tripleR    NaN         N        yes   
4297   9.5                               sb    -45         N        yes   

      sighting paint.mark   vial  \
3905       NaN       w.|t  17-84   
3918       NaN        w=a    nan   
3939       NaN        wva    nan   
3940       NaN       w||t  17-85   
4241       NaN       y.bc  16-62   
4297       NaN       y61b  16-60   

                                                                 misc  \
3905                                                              NaN   
3918  originally recorded as w?a before caught; B shed w loose scales   
3939                                  B rec shed w loose scales H & B   
3940                                   Bss w loose scales, T rec shed   
4241                                     nuchal pocket filled w mites   
4297  painted in "b" position by mistake; vial may be marked as 16-61   

     rtl_orig                 toes toe_pattern year  
3905        0                 9-13         NaN  nan  
3918        0  2017-12-16 00:00:00         NaN  nan  
3939        0                11-18         NaN  nan  
3940       36                 9-15         NaN  nan  
4241        0            1-6-11-20         NaN  nan  
4297       12              7-15-20         NaN  nan

Many of these appear to be from 2016/17, based on the toe vial numbers.  one may be from 2018, but we will need to confirm and determine if any of these have sufficient information to keep them in the data set.  For now we will drop them.

In [139]:
df.loc[idx_nntoes] = None
df.loc[idx_nntoes]

species toes_orig   sex date  svl  tl  rtl autotomized  mass location  \
3905    None      None  None  NaT  NaN NaN  NaN        None   NaN     None   
3918    None      None  None  NaT  NaN NaN  NaN        None   NaN     None   
3939    None      None  None  NaT  NaN NaN  NaN        None   NaN     None   
3940    None      None  None  NaT  NaN NaN  NaN        None   NaN     None   
4241    None      None  None  NaT  NaN NaN  NaN        None   NaN     None   
4297    None      None  None  NaT  NaN NaN  NaN        None   NaN     None   

     meters new.recap painted  sighting paint.mark  vial  misc rtl_orig  toes  \
3905   None      None    None       NaN       None  None  None     None  None   
3918   None      None    None       NaN       None  None  None     None  None   
3939   None      None    None       NaN       None  None  None     None  None   
3940   None      None    None       NaN       None  None  None     None  None   
4241   None      None    None       NaN       None  None  None     None  None   
4297   None      None    None       NaN       None  None  None     None  None   

     toe_pattern  year  
3905        None  None  
3918        None  None  
3939        None  None  
3940        None  None  
4241        None  None  
4297        None  None

<a id='AddCol'></a>

# Adding New Columns
[Top](#TOC)

We need to add new columns which we will use later in analyses:
- [TL_SVL](#TlSvl)
- [Mass_SVL](#MassSvl)
- [Lizard Number](#LizardNumber)
     - [assign lizard numbers](#Assign) 
     - [QC the lizard numbers](#QcLizNum) 
- [Days Since Capture](#daysSinceCapture)
- [Number of Captures](#capture)

<a id= 'TlSvl'></a>

## TL_SVL 
[Top](#TOC)

[Top Add Columns](#AddCol)



In [140]:
df['tl_svl']=(df.tl/df.svl)

<a id='MassSvl'></a>

## Mass_SVL
[Top](#TOC)

[Top Add Columns](#AddCol)



In [141]:
df['mass_svl']=(df.mass/df.svl)

<a id= 'LizardNumber'></a>

## Lizard Number
[Top](#TOC)

[Top Add Columns](#AddCol)

Here we use a set of functions to:
 - [assign lizard numbers](#Assign) to unique individuals (we repeat this step to ensure we have assigned all animals a number) and 
 - [QC the numbers](#QcLizNum) assigned.

<a id='Assign'></a>

### Assign lizard numbers
[Top](#TOC)

[Top Add Columns](#AddCol)

We make a first attempt at assigning lizard numbers.  We use the *lizsort* function to identify the subset of rows from the original dataset which have sufficient information to allow us to make an automated decision about the uniqueness of the individuals identified in those rows.  We name that df *sortable*.  The unsortable data are saved to a path as a file, *unsortable.csv*.  

In [142]:
sortable = lizsort(df, path = sourceinterDataBig)  


There were 3596 entries for which values for one of the critical criteria, (['species', 'toes', 'sex', 'date', 'svl']), were null.      These entries could not be evaluated and were written out to the file unsortable.csv for evaluation.


Next we call the *mindate* function on *sortable*.  This identifies the earliest date at which each unique combination of *sortCriteria* are recorded in a new column, *initialCaptureDate*.  The default sortCriteria are of the variables *species*, *toes*, and *sex*.  This also calculates and adds a column for *year_diff*, the difference in years between the initial capture date and the date value in a given row. 

In [143]:
sortable = mindate(sortable)

Next we call a the function *smallest*, which is analogous to *mindate*, but groups data in *sortable* into unique combinations of *species*, *toes*, *sex*, and *initialCaptureDate* before assigning the smallest SVL value recorded for each group to a new column for that group, *smallest_svl*.  *smallest* then calculates a new column *svl_diff* which is analogous to *year_diff*.

In [144]:
sortable = smallest(sortable)

Next we call the *validate* function on *sortable*, which applies a series of validation tests to the data, sequentially numbers unique combinations of *sortCriteria* and returns a dict containing uniquely numbered individuals and summary data.

In [145]:
tmp_sort = validate(sortable)
df_numbered1 = tmp_sort['val_data']


Of those entries we can handle, there are 1625 individuals as defined by ['species', 'toes', 'sex'] which pass validation based    on ['year_diff <= 7', 'svl_diff >= -2'] and 154 rows which do not pass validation.


### Second attempt to assign lizard numbers

[Top](#TOC)

[Top Add Columns](#AddCol)

Here we make a second attempt at assigning lizard numbers to ensure that all lizards have been assigned.  This second attempt is focused on those rows which were unvalidated during the first attempt *n_val_data*.  Since these are already a subset of those data which were sortable, we need only call the *mindate*, *smallest*, and *validate* functions.

In [146]:
n_val = mindate(tmp_sort['n_val_data'])
n_val = smallest(n_val)
df_numbered2 = validate(n_val)['val_data']


Of those entries we can handle, there are 45 individuals as defined by ['species', 'toes', 'sex'] which pass validation based    on ['year_diff <= 7', 'svl_diff >= -2'] and 0 rows which do not pass validation.


Since no rows remain unvalidated, we will not attempt a third validation.  We will simply append *df_numbered1* and *df_numbered2* to create *df_numbered* to create our full numbered dataset.

In [147]:
df_numbered = df_numbered1.append(df_numbered2,ignore_index=True,sort=False)
print("df:{}\ndf_numbered1:{}\ndf_numbered2:{}\ndf_numbered:{}".format(df.shape,df_numbered1.shape,df_numbered2.shape,
                                                               df_numbered.shape))
df_numbered.head()

df:(6299, 23)
df_numbered1:(2703, 27)
df_numbered2:(154, 27)
df_numbered:(2857, 27)


species  toes_orig sex       date   svl     tl   rtl autotomized  mass  \
0       j  2-6-12-15   m 2010-06-19  80.0  110.0  29.0        True  20.0   
1       j  2-9-15-17   f 2010-08-13  56.0   77.0   0.0       False   5.5   
2       j  3-6-11-17   m 2010-08-18  50.0   68.0   0.0       False   4.0   
3       j  3-6-15-16   f 2010-08-18  72.0   62.0  46.0        True  11.0   
4       j  3-6-12-17   m 2010-08-18  57.0   82.0   0.0       False   6.0   

                                         location meters new.recap painted  \
0                               10m v bottom bowl    -15         ?     yes   
1                                      20m up CCC    240         N     yes   
2                           1m vT at top R island    157         N     yes   
3  halfway between pool and 2 falls 2m up rt side    385         N     yes   
4                               R outcrop ^ oak R    425         N     yes   

   sighting paint.mark      vial                                       misc  \
0       NaN        y2c  03-10-cc  toe 15 missing at capture; possible recap   
1       NaN       y62c  61-10-cc                                        Tss   
2       NaN      y<c.t       nan                             Bss; lost toes   
3       NaN       y65c  65-10-cc                                        NaN   
4       NaN       y67c  66-10-cc                                        NaN   

  rtl_orig       toes toe_pattern  year    tl_svl  mass_svl  \
0       29  2-6-12-15         NaN  2010  1.375000  0.250000   
1        0  2-9-15-17         NaN  2010  1.375000  0.098214   
2        0  3-6-11-17         NaN  2010  1.360000  0.080000   
3       46  3-6-15-16         NaN  2010  0.861111  0.152778   
4        0  3-6-12-17         NaN  2010  1.438596  0.105263   

  initialCaptureDate  year_diff  svl_diff  liznumber  
0         2010-06-19          0       0.0        893  
1         2010-08-13          0       0.0        929  
2         2010-08-18          0       0.0        936  
3         2010-08-18          0       0.0        947  
4         2010-08-18          0       0.0        938

<a id='QcLizNum'></a>

### QC of lizard numbers
[Top](#TOC)

[Top Add Columns](#AddCol)

First we display the output data frame.

In [148]:
df_numbered

species                          toes_orig   sex       date    svl  \
0          j                          2-6-12-15     m 2010-06-19   80.0   
1          j                          2-9-15-17     f 2010-08-13   56.0   
2          j                          3-6-11-17     m 2010-08-18   50.0   
3          j                          3-6-15-16     f 2010-08-18   72.0   
4          j                          3-6-12-17     m 2010-08-18   57.0   
5          j                          3-6-15-17     m 2010-08-18   52.0   
6          j                          3-6-15-18     f 2010-08-18   53.0   
7          j                          3-6-15-19     f 2010-08-18   74.0   
8          j                          2-6-13-16     m 2010-08-19   55.0   
9          j                          2-6-14-17     m 2010-08-19   47.0   
10         j                          3-6-15-20     m 2010-08-19   56.0   
11         j                          2-6-12-20     f 2010-06-20   73.0   
12         j                                NaN     f 2010-06-20   62.0   
13         j                             2-6-16     m 2010-07-20   50.0   
14         j                             2-6-14     f 2010-07-20   47.0   
15         j                          2-9-13-16     m 2010-06-21   84.0   
16         j                          2-9-13-18     m 2010-06-21   75.0   
17         j                          2-9-13-19     f 2010-06-21   70.0   
18         j                          2-9-13-20     f 2010-06-21   57.0   
19         j                          3-6-12-18     f 2010-07-26   66.0   
20         j                         a3-6-12-19     m 2010-07-27   46.0   
21         j                          3-6-12-20     f 2010-07-27   63.0   
22         j                          3-6-13-16     m 2010-05-08   91.0   
23         j                          3-6-13-18     f 2010-05-08   68.0   
24         j                          3-6-13-19     m 2010-05-08   93.0   
25         j                          3-6-13-20     f 2010-05-08   48.0   
26         v                          3-7-15-16     f 2010-10-07   53.0   
27         v                          3-7-12-17     m 2010-08-13   56.0   
28         v                          3-7-11-16     f 2010-06-19   60.0   
29         v                          3-7-11-18     m 2010-06-19   49.0   
30         v                          3-7-11-19     m 2010-06-19   48.0   
31         v                          3-7-11-20     m 2010-06-20   46.0   
32         v                          3-7-12-16     f 2010-06-21   47.0   
33         v                          3-7-12-18     f 2010-06-21   55.0   
34         v                          3-7-12-19     m 2010-06-21   45.0   
35         v                          3-7-12-20     f 2010-06-21   50.0   
36         v                          3-8-12-19     m 2010-07-26   50.0   
37         v                          3-8-12-20     f 2010-07-26   54.0   
38         v                          3-8-15-16     m 2010-07-26   50.0   
39         v                          3-8-15-18     m 2010-07-27   51.0   
40         v                          3-8-15-20     f 2010-05-08   60.0   
41         v                          3-7-11-17     f 2010-05-08   55.0   
42         v                          3-8-15-19     f 2010-05-08   60.0   
43     other                               6-18     m 2010-08-13   51.0   
44     other                               6-20     m 2010-08-14   51.0   
45         j                          2-6-12-15     m 2010-10-07   86.0   
46         j                          1-6-15-17     f 2010-10-07   72.0   
47         j                            1-14-18     f 2010-10-07   79.0   
48         j                          1-7-11-16     m 2010-10-07   65.0   
49         j                            1-13-16     m 2010-10-07   90.0   
50         j                              12-19     m 2010-10-07   92.0   
51         j                             1-8-11     f 2010-10-07   75.0   
52         j                  

Identify individuals that have same species and toes, but different sex for review

In [149]:
df_numbered = df_numbered.merge(df_numbered.groupby(['species','toes']).sex.nunique().reset_index()\
                       .rename(columns = {'sex':'sex_count'}),how = 'inner', on = ['species','toes'])
df_numbered.loc[df_numbered.sex_count>1,:].to_csv('entries flagged with same species and toes diff sex.csv')
print("{} rows have the same species and toes but different values for sex"\
      .format(df_numbered.loc[df_numbered.sex_count>1,:].shape[0]))
df_numbered.head()

799 rows have the same species and toes but different values for sex


species  toes_orig sex       date   svl     tl   rtl autotomized  mass  \
0       j  2-6-12-15   m 2010-06-19  80.0  110.0  29.0        True  20.0   
1       j  2-6-12-15   m 2010-10-07  86.0  102.0  28.0        True  17.0   
2       j  2-9-15-17   f 2010-08-13  56.0   77.0   0.0       False   5.5   
3       j  3-6-11-17   m 2010-08-18  50.0   68.0   0.0       False   4.0   
4       j  3-6-15-16   f 2010-08-18  72.0   62.0  46.0        True  11.0   

                                         location meters new.recap painted  \
0                               10m v bottom bowl    -15         ?     yes   
1             6m v bottoom bowl right side 4 m up    NaN         R     yes   
2                                      20m up CCC    240         N     yes   
3                           1m vT at top R island    157         N     yes   
4  halfway between pool and 2 falls 2m up rt side    385         N     yes   

   sighting paint.mark      vial                                       misc  \
0       NaN        y2c  03-10-cc  toe 15 missing at capture; possible recap   
1       NaN       y22c       nan            loose scale on ventrum and head   
2       NaN       y62c  61-10-cc                                        Tss   
3       NaN      y<c.t       nan                             Bss; lost toes   
4       NaN       y65c  65-10-cc                                        NaN   

  rtl_orig       toes toe_pattern  year    tl_svl  mass_svl  \
0       29  2-6-12-15         NaN  2010  1.375000  0.250000   
1       28  2-6-12-15         NaN  2010  1.186047  0.197674   
2        0  2-9-15-17         NaN  2010  1.375000  0.098214   
3        0  3-6-11-17         NaN  2010  1.360000  0.080000   
4       46  3-6-15-16         NaN  2010  0.861111  0.152778   

  initialCaptureDate  year_diff  svl_diff  liznumber  sex_count  
0         2010-06-19          0       0.0        893          1  
1         2010-06-19          0       6.0        893          1  
2         2010-08-13          0       0.0        929          1  
3         2010-08-18          0       0.0        936          1  
4         2010-08-18          0       0.0        947          1

In [150]:
print("Lizard Numbers in the sample range from {} to {}."\
      .format(df_numbered.liznumber.min(),df_numbered.liznumber.max()))

Lizard Numbers in the sample range from 1 to 1625.


In [151]:
possibleLizNum = set(range(int(df_numbered.liznumber.min()),int(df_numbered.liznumber.max())))
actualLizNum = set(pd.Series(df_numbered.liznumber.unique()).dropna().apply(int))
print("\nThere are {} entries.  There are {} unique lizard numbers.\
\n\nThe liznumber ranges from {} to {}."\
  .format(df_numbered.shape[0],len(df_numbered.liznumber.unique())\
          ,df_numbered.liznumber.min(),df_numbered.liznumber.max()))

missingLizNum = possibleLizNum - actualLizNum
if len(missingLizNum)>0:
    print("\n\nThe following numbers are not assigned to a lizard:\n{}"\
      .format(missingLizNum))
else:
    print("\n\nThere are no numbers which were not assigned.")


There are 2857 entries.  There are 1625 unique lizard numbers.

The liznumber ranges from 1 to 1625.


There are no numbers which were not assigned.


<a id='daysSinceCapture'></a>

### Days Since Capture
[Top](#TOC)

[Top Add Columns](#AddCol)

*daysSinceCapture* identifies the number of days since the animal was captured

In [152]:
df_numbered.loc[:,'daysSinceCapture'] = (df_numbered.date - df_numbered.initialCaptureDate).dt.days

<a id='capture'></a>

### Capture Number
[Top](#TOC)

[Top Add Columns](#AddCol)

*capture* identifies the number of times an animal has been captured prior to an entry.
We will need to [QC capture](#QcCapture) as well.

In [153]:
# need to QC this this seems to be leading to several cases in which recap individuals that 
# only have one capture
df_numbered['capture'] = df_numbered.sort_values(['liznumber','date'])\
.groupby(['liznumber']).daysSinceCapture.cumcount()+1

In [154]:
print(df_numbered.loc[df_numbered.species.isin(['j','v'])].groupby('capture').capture.count())

capture
1     1492
2      452
3      186
4       81
5       41
6       20
7       13
8       10
9        8
10       8
11       8
12       8
13       8
14       8
15       8
16       8
17       8
18       7
19       7
20       7
21       7
22       7
23       6
24       6
25       6
26       6
27       5
28       5
29       5
30       5
31       5
32       4
33       4
34       4
35       4
36       4
37       4
38       4
39       4
40       4
41       4
42       4
43       4
44       4
45       4
46       4
47       4
48       4
49       4
50       4
51       4
52       4
53       4
54       4
55       4
56       4
57       4
58       3
59       3
60       3
61       3
62       3
63       3
64       3
65       3
66       3
67       3
68       3
69       3
70       2
71       2
72       2
73       2
74       2
75       2
76       2
77       2
78       2
79       2
80       2
81       2
82       2
83       1
84       1
85       1
86       1
87       1
88       1
Name: capture, dtype: in

Let's QC these numbers by looking at the distribution of the number of captures.

In [156]:
Sj = go.Histogram(x = df_numbered.loc[(df_numbered.species=='j')].groupby('liznumber').capture.max(),name='Sj')
Sv = go.Histogram(x = df_numbered.loc[(df_numbered.species=='v')].groupby('liznumber').capture.max(),name='Sv')

data = [Sj,Sv]
layout = go.Layout(
    title = 'Histogram of Maximum Number of Captures for CC 2000-2017',
    titlefont = dict(
        size = 20),
    xaxis = dict(
        dtick = 1,
        title = 'Maximum Number of Captures',
        titlefont = dict(
            size = 18)),
    yaxis = dict(
        title = 'Number of Unique Lizards',
        titlefont = dict(
            size = 18)))

fig = go.Figure(
        data = data,
        layout = layout)
py.iplot(fig, filename = 'Histogram of Maximum Number of Captures for CC 2000-2017')

Now we'll display all data points associated with lizards who have more than 8 captures reported.

In [194]:
threshold = 8
immortals = df_numbered.loc[df_numbered.capture>threshold].liznumber.unique()
df_immortals = df_numbered.loc[df_numbered.liznumber.isin(immortals)]
print("There are {} lizards with greater than {} captures.  They account for {} rows of data.\n"\
      .format(df_immortals.liznumber.nunique(),threshold,df_immortals.shape[0]))
df_immortals = df_immortals.loc[:,[ 'liznumber','capture','species', 'toes_orig', 'toes','sex', 'date', 'svl_diff', 'tl', 'rtl_orig',
       'meters', 'new.recap','sighting', 'vial', 'misc','initialCaptureDate','year_diff', 'sex_count',
                  'daysSinceCapture','year']].sort_values(['liznumber','year'])
df_immortals

There are 11 lizards with greater than 8 captures.  They account for 439 rows of data.



liznumber  capture species                          toes_orig  \
1587         19        1       j                         1-10-14-16   
185          19        8       j                    4 - 6 - 11 - 20   
188          19       18       j                    4 - 6 - 12 - 19   
190          19       25       j                    4 - 6 - 13 - 17   
191          19       23       j                    4 - 6 - 13 - 19   
192          19        2       j                       b 1 - 6 - 11   
194          19        3       j                  b 4 - 6 - 11 - 16   
197          19       15       j                  b 4 - 6 - 12 - 17   
199          19        4       j                         1 - 8 - 11   
200          19       16       j                         2 - 8 - 13   
201          19       26       j                         3 - 7 - 15   
202          19       20       j                         3 - 9 - 15   
203          19        5       j                             1 - 12   
204          19       21       j                        1 - 12 - 17   
206          19        6       j                    1 - 7 - 13 - 18   
208          19       24       j                    2 - 6 - 12 - 20   
209          19        7       j                    2 - 9 - 15 - 20   
210          19       17       j                    3 - 7 - 15 - 16   
211          19        9       j                    4 - 6 - 11 - 19   
213          19       22       j                    b - 4 - 11 - 20   
216          19       19       j                  b 1 - 6 - 15 - 17   
217          19       10       j                       b 1 - 7 - 11   
218          19       11       j                  b 1 - 7 - 11 - 19   
222          19       12       j                  b 2 - 9 - 15 - 17   
223          19       13       j                  b 2 - 9 - 15 - 19   
226          19       14       j                      b 6 - 14 - 20   
173          19       27       j                           7 -11-17   
174          19       28       j                            5 11 16   
175          19       29       j                             5 6 16   
176          19       30       j                            5 13 17   
178          19       31       j                             5 6 17   
1592         20        1       j                         1-10-14-17   
183          20        7       j                         4 - 6 - 12   
184          20       18       j                         4 - 6 - 13   
186          20        8       j                    4 - 6 - 12 - 16   
187          20       14       j                    4 - 6 - 12 - 18   
189          20       20       j                    4 - 6 - 13 - 16   
193          20        2       j                       b 4 - 6 - 11   
195          20        3       j                  b 4 - 6 - 11 - 17   
196          20        4       j                  b 4 - 6 - 11 - 18   
198          20       17       j                  b 4 - 6 - 12 - 20   
205          20        5       j                       1 - 15  - 17   
207          20        6       j                    1 - 7 - 14 - 19   
212          20       19       j                b - 2 - 7 - 13 - 20   
214          20        9       j                      b 1 - 10 - 17   
215          20       15       j                      b 1 - 14 - 17   
219          20       10       j                  b 1 - 7 - 14 - 18   
220          20       16       j                  b 1 - 7 - 15 - 20   
221          20       11       j                  b 1 - 9 - 11 - 20   
224          20       12       j                  b 3 - 6 - 11 - 17   
225          20       13       j                  b 3 - 6 - 11 - 20   
177          20       21       j                          4 6 12 20   
179          20       22       j                             5 6 18   
180          20       23       j                             5 7 13   
181          20       24       j                            8 13 19   
182          20       25      

We will export these for further inspection using the *[exportliz](#exportliz)* function.

In [193]:
exportliz(df_immortals,iterator='liznumber')

<a id='yearstoolarge'></a>

### years too large
[Top](#TOC)

In [ ]:
yeartoomuch = df_numbered.loc[df_numbered.year_diff>=5,'liznumber']
checkyears = df_numbered.loc[df_numbered.liznumber.isin(yeartoomuch)].sort_values(['liznumber'])
checkyears.to_csv('check years.csv')
checkyears

In [ ]:
jarrovii = go.Histogram(x = df_numbered.loc[df_numbered.species.isin(['j'])].groupby('liznumber')\
                     .year_diff.max(),name = 'S. jarrovii')
virgatus = go.Histogram(x = df_numbered.loc[df_numbered.species.isin(['v'])].groupby('liznumber')\
                     .year_diff.max(), name = 'S. virgatus')
data = [jarrovii, virgatus]
layout = go.Layout(
    title = 'Number of Individuals by Years Between First and Last Capture 2000-2017',
    titlefont = dict(
        size = 20),
    xaxis = dict(
        dtick = 1,
        title = 'Maximum Number of Years Since Initial Capture',
        titlefont = dict(
            size = 18)),
    yaxis = dict(
        title = 'Number of Lizards',
        titlefont = dict(
            size = 18))
)
fig = go.Figure(
        data = data,
        layout = layout)
py.iplot(fig, filename = 'Frequency of Captures in Crystal Creek 2000 - 2017 (by species)')

Should we drop this figure entirely.  Not sure this is useful.

In [ ]:
# Freeze work on this figure until we've resolved issues with calculation based on year
# ADD HORIZONTAL LINES FOR EACH YEAR
j_lizards = go.Scatter(x = df_numbered.loc[df_numbered.species.isin(['j'])].liznumber,
                   y = df_numbered.loc[df_numbered.species.isin(['j'])]\
                      .groupby('liznumber').daysSinceCapture.max(), 
                     mode = 'markers', name='S. jarrovii')
v_lizards = go.Scatter(x = df_numbered.loc[df_numbered.species.isin(['v'])].liznumber,
                   y = df_numbered.loc[df_numbered.species.isin(['v'])]\
                      .groupby('liznumber').daysSinceCapture.max(), 
                     mode = 'markers', name='S. virgatus')
# year1 = go.Scatter(x=[df_numbered.liznumber.min(),df_numbered.liznumber.max()],y = (365))
# year2 = go.Scatter(y = 365*2)
# year3 = go.Scatter(y = 365*3)
# year4 = go.Scatter(y = 365*4)
# year5 = go.Scatter(y = 365*5)
# year6 = go.Scatter(y = 365*6)
# year7 = go.Scatter(y = 365*7)
# year8 = go.Scatter(y = 365*8)

# data = [j_lizards, v_lizards, year1, year2, year3, year4, year5, year6, year7, year8]
data = [j_lizards, v_lizards]
layout = go.Layout(
    title = 'Days Since Initial Capture in Crystal Creek 2000 - 2017',
        titlefont = dict(
            size = 20),
    xaxis = dict(
            title='Lizard Number',
            titlefont=dict(
                size=18)),
    yaxis = dict(
            title='Greatest Number of Days Since<br> Initial Capture',
            titlefont=dict(
                size=18)))

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename = 'Days Since Initial Capture in Crystal Creek 2000 - 2017')

Drop this figure as well?

In [ ]:
dfF = df_numbered.loc[(df_numbered.sex =='f' )& (df_numbered.species.isin(['j','v']))]
dfM = df_numbered.loc[(df_numbered.sex =='m') & (df_numbered.species.isin(['j','v']))]

In [ ]:
# Freeze work on this figure until we've resolved issues with calculation based on year
females = go.Scatter(
    x = dfF.liznumber,
    y = dfF.groupby('liznumber').daysSinceCapture.max(),
    name = 'females',
    mode = 'markers',
    marker = dict(
        color = 'rgba(152, 0, 0, .8)',
        opacity = 0.75,
        line = dict(
            width = 2,
            color = 'rgb(0, 0, 0)'
        )
    )
)

males = go.Scatter(
    x = dfM.liznumber,
    y = dfM.groupby('liznumber').daysSinceCapture.max(),
    name = 'males',
    mode = 'markers',
    marker = dict(
        color = 'rgba(255, 182, 193, .9)',
        opacity = 0.75,
        line = dict(
            width = 2,
        )
    )
)

data = [females, males]

layout = dict(title = 'Days Since Initial Capture in Crystal Creek 2000 - 2017 By Sex',
              yaxis = dict(
                  title='Greatest Number of Days Since<br> Initial Capture',
                  titlefont=dict(
                      size=18)
              ),
              xaxis = dict(zeroline = False)
             )

fig = dict(data=data, layout=layout)
py.iplot(fig, filename='Days Since Initial Capture in Crystal Creek 2000 - 2017 By Sex')

In [ ]:

males = go.Histogram(x = df_numbered.loc[(df_numbered.sex == 'm')& (df_numbered.species.isin(['j','v']))
                                                                    ,'year']
                     ,opacity= 0.75,name='males')
females = go.Histogram(x = df_numbered.loc[(df_numbered.sex == 'f')& (df_numbered.species.isin(['j','v']))
                                                                      ,'year']
                       , opacity= 0.75, name = 'females')
data = [males,females]
py.iplot(data, filename = 'Distribution of Sex by Year in Crystal Creek 2000 - 2017')

In [ ]:
column_order = ['liznumber','date','initialCaptureDate',]

In [ ]:
df.year.value_counts(dropna=False).reset_index()

<a id='QcCapture'></a>

### QC of Capture number and Recap status
[Top](#TOC)

[Top Add Columns](#AddCol)

[Top Capture Number](#capture)

In [ ]:
recapQuestion=df_numbered\
.loc[(df_numbered.capture==1 )&(df_numbered['new.recap']=='recap')&(df_numbered.species.isin(['j','v'])),:]
print("There are {} instances in rows for which a lizard appears to have only one capture, \
but is listed as a recap.\
The distribution of these across years in the sample is as follows:\n{}."\
      .format(recapQuestion.shape[0],recapQuestion.year.value_counts()))
recapQuestion.to_csv("Questionable recaptures.csv")#These individuals need to be rechecked in the raw notes
recapQuestion.head()

<a id='exportFinal'></a>

# Export Cleaned data
[Top](#TOC)

Now we export the cleaned data to a csv.

In [ ]:
df_numbered = df_numbered.rename(index = str, columns = {'new.recap':'newRecap'})
qc_drop_cols = df_numbered.columns[df_numbered.columns.str.contains('force|drop')]
df_full = df_numbered.drop(qc_drop_cols,1)

In [ ]:
os.chdir(outputBig)
timestamp = (pd.to_datetime('now')-pd.Timedelta(hours=4))
timestamp = str(timestamp)[:-10].replace(':','hrs')+'min'
filename = 'cleaned CC data 2000-2017_' + timestamp+ '.csv'
df_full.to_csv(filename,index = False)
filename